# Farina in Natura - estratégia

![](Logo_farina_in_natura_edited.jpg)

## Importando os dados e observações iniciais

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns; sns.set()
import datetime
import nbformat
import chart_studio
import plotly.express as px
import cufflinks as cf
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode (connected = True )
cf.go_offline()
# chart_studio.tools.set_credentials_file(username='claudio.oliveira', api_key='fXrLqCmkdJQyTheCzYMS')
from IPython.display import display


In [2]:
from fpdf import FPDF

In [3]:
from IPython.display import display
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [4]:
# para resolver o problema: "(unicode error) 'utf-8' codec can't decode "
# https://www.youtube.com/watch?v=ZSC7X4N8RKo,
#Erro: 
# UnicodeDecodeError: 'utf-8' codec can't decode byte 0xe9 in position 900: invalid continuation byte
# enem = pd.read_csv("MICRODADOS_ENEM_2020.csv", encoding="utf-8", sep = ';')
# enem = pd.read_csv("MICRODADOS_ENEM_2020.csv", encoding="ISO-8859-1", sep = ';')

transactions = pd.read_csv(r'C:\Users\ctobr\OneDrive\DATA_Science\1_farina_in_natura\farina_in_natura00\CSV\farina.CSV', 
encoding="ISO-8859-1", sep = ';')

In [5]:
transactions.head()

venda         data_hora     cliente mesa   item                produto  \
0  460.0  01/02/2022 08:13  CONSUMIDOR  M 1  119.0  SUCO DE LARANJA 400ML   
1  460.0  01/02/2022 08:13  CONSUMIDOR  M 1  121.0     PAO SOURDOUGH OVOS   
2  461.0  01/02/2022 08:14  CONSUMIDOR  M 2  119.0  SUCO DE LARANJA 400ML   
3  461.0  01/02/2022 08:14  CONSUMIDOR  M 2  121.0     PAO SOURDOUGH OVOS   
4  465.0  01/02/2022 09:01  CONSUMIDOR  M 1   46.0       QUICHE BACON 90G   

   quantidade valor_unit  desconto total_item  
0         1.0       14,5       0.0       14,5  
1         1.0       15,5       0.0       15,5  
2         1.0       14,5       0.0       14,5  
3         1.0       15,5       0.0       15,5  
4         2.0       19,5       0.0         39

In [6]:
transactions.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 25998 entries, 0 to 25997
Data columns (total 10 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   venda       25992 non-null  float64
 1   data_hora   25992 non-null  object 
 2   cliente     25992 non-null  object 
 3   mesa        22779 non-null  object 
 4   item        25922 non-null  float64
 5   produto     25992 non-null  object 
 6   quantidade  25992 non-null  float64
 7   valor_unit  25992 non-null  object 
 8   desconto    25992 non-null  float64
 9   total_item  25992 non-null  object 
dtypes: float64(4), object(6)
memory usage: 2.0+ MB


# Limpeza e manipulação dos dados

In [7]:
### CHECK OUT IF THE NUMBER OF TOTAL ENTRIES IS EQUAL TO THE NUMBER OF ENTRIES OF THE VARIABLES  

transactions.isnull().sum()

venda            6
data_hora        6
cliente          6
mesa          3219
item            76
produto          6
quantidade       6
valor_unit       6
desconto         6
total_item       6
dtype: int64

In [8]:
## DROPPING THE ROWS THAT ALL COLUMN VALUES ARE NULL
#  https://www.youtube.com/watch?v=uDr67HBIPz8&t=818s

transactions = transactions.dropna(how='all')

In [9]:
# Delete the column "item"

del transactions["item"]

In [10]:
transactions.info()
transactions.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 9 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   venda       25992 non-null  float64
 1   data_hora   25992 non-null  object 
 2   cliente     25992 non-null  object 
 3   mesa        22779 non-null  object 
 4   produto     25992 non-null  object 
 5   quantidade  25992 non-null  float64
 6   valor_unit  25992 non-null  object 
 7   desconto    25992 non-null  float64
 8   total_item  25992 non-null  object 
dtypes: float64(3), object(6)
memory usage: 2.0+ MB


venda         data_hora     cliente mesa                produto  \
0  460.0  01/02/2022 08:13  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML   
1  460.0  01/02/2022 08:13  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS   
2  461.0  01/02/2022 08:14  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML   
3  461.0  01/02/2022 08:14  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS   
4  465.0  01/02/2022 09:01  CONSUMIDOR  M 1       QUICHE BACON 90G   

   quantidade valor_unit  desconto total_item  
0         1.0       14,5       0.0       14,5  
1         1.0       15,5       0.0       15,5  
2         1.0       14,5       0.0       14,5  
3         1.0       15,5       0.0       15,5  
4         2.0       19,5       0.0         39

In [11]:
## Using isna() to select all rows with NaN in the column ('mesa') and the value "CONSUMIDOR" on the column "cliente" 
## and replace the "mesa" value with "M0"
## https://datatofish.com/rows-with-nan-pandas-dataframe/
## https://www.geeksforgeeks.org/how-to-replace-values-in-column-based-on-condition-in-pandas/

transactions.loc[(transactions["cliente"] == 'CONSUMIDOR') &  (transactions['mesa'].isna()), 'mesa']= 'M0'


In [12]:
# Checking if the changes were correct.

transactions.loc[transactions["mesa"] == 'M0']

venda         data_hora     cliente mesa                      produto  \
121  520.0  02/02/2022 16:57  CONSUMIDOR   M0        BOMBOLONI NUTELLA 80G   
122  520.0  02/02/2022 16:57  CONSUMIDOR   M0    TARTELETE DE MORANGO 120G   
123  520.0  02/02/2022 16:57  CONSUMIDOR   M0      CROISSANT MUSSATRELA DE   
894  856.0  11/02/2022 19:19  CONSUMIDOR   M0  CROISSANT BRIE PARMA MEL DE   
895  856.0  11/02/2022 19:19  CONSUMIDOR   M0    VH SANTA HORTENSIA SAUVIG   

     quantidade valor_unit  desconto total_item  
121         2.0         12       0.0         24  
122         1.0         18       0.0         18  
123         1.0       25,5       0.0       25,5  
894         2.0       25,5       0.0         51  
895         1.0         59       0.0         59

In [13]:
# Assigning a value "ND" to the empty records in column "mesa"
# https://www.w3schools.com/python/pandas/pandas_cleaning_empty_cells.asp

transactions['mesa'].fillna("ND",inplace = True )

In [14]:
# Convert the "venda" variable from float64 type to integer type
# https://stackoverflow.com/questions/43956335/convert-float64-column-to-int64-in-pandas

transactions['venda'] = np.int64(transactions['venda'])

In [15]:
# Convert the "quantidade" variable from float64 type to integer type
# https://stackoverflow.com/questions/43956335/convert-float64-column-to-int64-in-pandas

transactions['quantidade'] = np.int64(transactions['quantidade'])

In [16]:
# change the decimal separator of the the variable "valor_unit" from "," to "."
# https://cursos.alura.com.br/forum/topico-transformar-pontos-por-virgulas-dentro-de-um-dataframe-121090
transactions['valor_unit'] = transactions['valor_unit'].str.replace(",",".")

# Convert the "valor_uni" variable from object type to float64 type
# https://www.statology.org/pandas-convert-object-to-float/

transactions['valor_unit'] = transactions['valor_unit'].astype(float)

In [17]:
# change the decimal delimiter of the the variable "total_item" from "," to "."
# https://cursos.alura.com.br/forum/topico-transformar-pontos-por-virgulas-dentro-de-um-dataframe-121090
transactions['total_item'] = transactions['total_item'].str.replace(",",".")

# Convert the "total_item" variable from object type to float64 type
# https://www.statology.org/pandas-convert-object-to-float/

transactions['total_item'] = transactions['total_item'].astype(float)

In [18]:


# Convert "data_hora" to datetime object
transactions['data_hora'] = pd.to_datetime(transactions['data_hora'], format='%d/%m/%Y %H:%M')

# Creating a horario column that is a copy of data_hora and coverting it to datetime and extracting only the day;
transactions['horario'] = (transactions['data_hora'])
transactions['horario'] = transactions['horario'].dt.date

#How to Solve Python ValueError: unconverted data remains
#read://https_researchdatapod.com/?url=https%3A%2F%2Fresearchdatapod.com%2Fhow-to-solve-python-valueerror-unconverted-data-remains%2F

In [19]:
transactions.head()

venda           data_hora     cliente mesa                produto  \
0    460 2022-02-01 08:13:00  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML   
1    460 2022-02-01 08:13:00  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS   
2    461 2022-02-01 08:14:00  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML   
3    461 2022-02-01 08:14:00  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS   
4    465 2022-02-01 09:01:00  CONSUMIDOR  M 1       QUICHE BACON 90G   

   quantidade  valor_unit  desconto  total_item     horario  
0           1        14.5       0.0        14.5  2022-02-01  
1           1        15.5       0.0        15.5  2022-02-01  
2           1        14.5       0.0        14.5  2022-02-01  
3           1        15.5       0.0        15.5  2022-02-01  
4           2        19.5       0.0        39.0  2022-02-01

In [20]:
transactions.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 10 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   venda       25992 non-null  int64         
 1   data_hora   25992 non-null  datetime64[ns]
 2   cliente     25992 non-null  object        
 3   mesa        25992 non-null  object        
 4   produto     25992 non-null  object        
 5   quantidade  25992 non-null  int64         
 6   valor_unit  25992 non-null  float64       
 7   desconto    25992 non-null  float64       
 8   total_item  25992 non-null  float64       
 9   horario     25992 non-null  object        
dtypes: datetime64[ns](1), float64(3), int64(2), object(4)
memory usage: 2.2+ MB


In [21]:

# https://www.dataquest.io/blog/python-datetime-tutorial/


# add hora and minuto column; using class attributes .hour and .minute

transactions['hora'] = transactions.data_hora.dt.hour
transactions['minuto'] = transactions.data_hora.dt.minute



### Creating a column name 'hora_minuto'

In [22]:
# https://gist.github.com/krisbolton/aef6179ecf906892565d326b979b3a5b
# https://www.youtube.com/watch?v=TbXaP56Omuc


transactions['hora_minuto']=pd.to_datetime(transactions['data_hora'])

transactions['hora_minuto'] = transactions['hora_minuto'].dt.time

In [23]:
transactions.head()

venda           data_hora     cliente mesa                produto  \
0    460 2022-02-01 08:13:00  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML   
1    460 2022-02-01 08:13:00  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS   
2    461 2022-02-01 08:14:00  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML   
3    461 2022-02-01 08:14:00  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS   
4    465 2022-02-01 09:01:00  CONSUMIDOR  M 1       QUICHE BACON 90G   

   quantidade  valor_unit  desconto  total_item     horario  hora  minuto  \
0           1        14.5       0.0        14.5  2022-02-01     8      13   
1           1        15.5       0.0        15.5  2022-02-01     8      13   
2           1        14.5       0.0        14.5  2022-02-01     8      14   
3           1        15.5       0.0        15.5  2022-02-01     8      14   
4           2        19.5       0.0        39.0  2022-02-01     9       1   

  hora_minuto  
0    08:13:00  
1    08:13:00  
2    08:14:00  
3    08:14:00  
4    09:01:00

In [24]:
transactions.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 13 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   venda        25992 non-null  int64         
 1   data_hora    25992 non-null  datetime64[ns]
 2   cliente      25992 non-null  object        
 3   mesa         25992 non-null  object        
 4   produto      25992 non-null  object        
 5   quantidade   25992 non-null  int64         
 6   valor_unit   25992 non-null  float64       
 7   desconto     25992 non-null  float64       
 8   total_item   25992 non-null  float64       
 9   horario      25992 non-null  object        
 10  hora         25992 non-null  int64         
 11  minuto       25992 non-null  int64         
 12  hora_minuto  25992 non-null  object        
dtypes: datetime64[ns](1), float64(3), int64(4), object(5)
memory usage: 2.8+ MB


### Renaming the column "data_hora" to "data"

In [25]:
# https://www.statology.org/pandas-rename-columns/
# renaming the column

transactions.rename(columns = {'data_hora':'data'}, inplace = True)


### Extracting only the Date from 'data' column

In [26]:

## https://datagy.io/pandas-extract-date-from-datetime/
transactions['data'] = transactions['data'].dt.normalize()

In [27]:
# Definindo a função time_of_day
def time_of_day(hora):
    """
    Determina se a  compra foi feita pela manhã, tarde ou noite.
    """
    
    if hora < 12:
        
        return 'manhã'
    
    elif hora < 17:
        
        return 'tarde'
    
    else:
        
        return 'noite'

In [28]:
# Apply time of day function to 'hora' column

transactions['time_of_day'] = transactions.hora.apply(time_of_day)


In [29]:
# https://pt.stackoverflow.com/questions/508484/mostrar-dias-da-semana#:~:text=Como%20weekday()%20retorna%20um,fim%20de%20semana%20ou%20n%C3%A3o.

import locale
# setar locale para português para que os dias da semana retornem em portugês no código abaixo.
locale.setlocale(locale.LC_ALL, 'pt_BR.utf8')

'pt_BR.utf8'

In [30]:
# Add a day of week variable and a second classifier of weekday or weekend

from datetime import date
import calendar

transactions['day_of_week'] = [calendar.day_name[i.weekday()] for i in transactions['horario']]


In [31]:
transactions.head()

venda       data     cliente mesa                produto  quantidade  \
0    460 2022-02-01  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML           1   
1    460 2022-02-01  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS           1   
2    461 2022-02-01  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML           1   
3    461 2022-02-01  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS           1   
4    465 2022-02-01  CONSUMIDOR  M 1       QUICHE BACON 90G           2   

   valor_unit  desconto  total_item     horario  hora  minuto hora_minuto  \
0        14.5       0.0        14.5  2022-02-01     8      13    08:13:00   
1        15.5       0.0        15.5  2022-02-01     8      13    08:13:00   
2        14.5       0.0        14.5  2022-02-01     8      14    08:14:00   
3        15.5       0.0        15.5  2022-02-01     8      14    08:14:00   
4        19.5       0.0        39.0  2022-02-01     9       1    09:01:00   

  time_of_day  day_of_week  
0       manhã  terça-feira  
1       manhã  terça-feira  
2       manhã  terça-feira  
3       manhã  terça-feira  
4       manhã  terça-feira

In [32]:

transactions['day_type'] = ['FDS' if (i == 'domingo') | (i == 'sábado') else 'DDS' for i in 
                                                                            transactions['day_of_week']]


In [33]:
transactions.rename(columns = {'day_of_week':'dia_da_semana'}, inplace = True)

In [34]:
transactions.rename(columns = {'time_of_day':'hora_do_dia'}, inplace = True)

In [35]:
transactions.rename(columns = {'day_type':'tipo_de_dia'}, inplace = True)

In [36]:
# Add an item count variable equal to one for future groupby operations

transactions['item_count'] = 1


In [37]:
transactions.head()

venda       data     cliente mesa                produto  quantidade  \
0    460 2022-02-01  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML           1   
1    460 2022-02-01  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS           1   
2    461 2022-02-01  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML           1   
3    461 2022-02-01  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS           1   
4    465 2022-02-01  CONSUMIDOR  M 1       QUICHE BACON 90G           2   

   valor_unit  desconto  total_item     horario  hora  minuto hora_minuto  \
0        14.5       0.0        14.5  2022-02-01     8      13    08:13:00   
1        15.5       0.0        15.5  2022-02-01     8      13    08:13:00   
2        14.5       0.0        14.5  2022-02-01     8      14    08:14:00   
3        15.5       0.0        15.5  2022-02-01     8      14    08:14:00   
4        19.5       0.0        39.0  2022-02-01     9       1    09:01:00   

  hora_do_dia dia_da_semana tipo_de_dia  item_count  
0       manhã   terça-feira         DDS           1  
1       manhã   terça-feira         DDS           1  
2       manhã   terça-feira         DDS           1  
3       manhã   terça-feira         DDS           1  
4       manhã   terça-feira         DDS           1

In [38]:
transactions.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 17 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   venda          25992 non-null  int64         
 1   data           25992 non-null  datetime64[ns]
 2   cliente        25992 non-null  object        
 3   mesa           25992 non-null  object        
 4   produto        25992 non-null  object        
 5   quantidade     25992 non-null  int64         
 6   valor_unit     25992 non-null  float64       
 7   desconto       25992 non-null  float64       
 8   total_item     25992 non-null  float64       
 9   horario        25992 non-null  object        
 10  hora           25992 non-null  int64         
 11  minuto         25992 non-null  int64         
 12  hora_minuto    25992 non-null  object        
 13  hora_do_dia    25992 non-null  object        
 14  dia_da_semana  25992 non-null  object        
 15  tipo_de_dia    2599

# Verificando alguma divergência dos dados

In [39]:
# Verificando se o valor "total_item" é igual a: "quantidade" * "valor_unit"

transactions["total_item_verif"] = transactions['quantidade']* transactions['valor_unit']

In [40]:
# Continuando o item anterior
# https://www.dataquest.io/blog/tutorial-add-column-pandas-dataframe-based-on-if-else-condition/

transactions['confirm'] = np.where(transactions['total_item'] > transactions['total_item_verif'], True, False)


In [41]:
# continuando o item anterior
resumo = transactions.loc[transactions["confirm"] == True].sum()
print (resumo)

venda                                                        13730391
cliente             CONSUMIDORCONSUMIDORCONSUMIDORCONSUMIDORIFOODC...
mesa                M 5M 13M 11M 5NDM 19NDM 13M 13M 17NDM 23M 23M ...
produto             CROISSANTCROISSANTCROISSANTCROISSANTCROISSANT ...
quantidade                                                       2139
valor_unit                                                    21083.7
desconto                                                          0.0
total_item                                                    53878.3
hora                                                            29332
minuto                                                          59296
hora_do_dia         manhãmanhãtardemanhãmanhãmanhãmanhãnoitenoiten...
dia_da_semana       sexta-feirasexta-feirasexta-feirasábadosábados...
tipo_de_dia         DDSDDSDDSFDSFDSFDSFDSFDSFDSFDSFDSFDSFDSFDSFDSF...
item_count                                                       2032
total_item_verif    

C:\Users\ctobr\AppData\Local\Temp\ipykernel_38380\2200306820.py:2: FutureWarning:

The default value of numeric_only in DataFrame.sum is deprecated. In a future version, it will default to False. In addition, specifying 'numeric_only=None' is deprecated. Select only valid columns or specify the value of numeric_only to silence this warning.



In [42]:
# Gerando um relatório em pdf dos dados divergentes
# How do I select specific rows and columns from a DataFrame?
# https://pandas.pydata.org/docs/getting_started/intro_tutorials/03_subset_data.html#how-do-i-select-specific-rows-and-columns-from-a-dataframe
# https://www.geeksforgeeks.org/select-rows-columns-by-name-or-index-in-pandas-dataframe-using-loc-iloc/

ts2 = transactions.loc[transactions["confirm"] == True, ["venda", "produto", "quantidade", "valor_unit", "total_item", "total_item_verif"]]

In [43]:
# Exporting to a pdf file the transactions that has a inconsistent data.
from matplotlib.backends.backend_pdf import PdfPages


In [44]:
# https://levelup.gitconnected.com/how-to-write-a-pandas-dataframe-as-a-pdf-5cdf7d525488

def _draw_as_table(df, pagesize):
    alternating_colors = [['white'] * len(df.columns), ['lightgray'] * len(df.columns)] * len(df)
    alternating_colors = alternating_colors[:len(df)]
    fig, ax = plt.subplots(figsize=pagesize)
    ax.axis("tight")
    ax.axis('off')
    the_table = ax.table(cellText=df.values,
                        rowLabels=df.index,
                        colLabels=df.columns,
                        rowColours=['lightblue']*len(df),
                        colColours=['lightblue']*len(df.columns),
                        cellColours=alternating_colors,
                        loc='center')
    return fig


In [45]:
# https://www.alixaprodev.com/2022/05/convert-pandas-dataframe-to-pdf-in-python.html
#fig, ax =plt.subplots(figsize=(14,6))
#ax.axis('equal')
#ax.axis('off')
#the_table = ax.table(cellText=ts2.values,colLabels=ts2.columns,loc='center')




In [46]:
def dataframe_to_pdf(df, filename, numpages=(1, 1), pagesize=(11, 8.5)):
  with PdfPages(filename) as pdf:
    nh, nv = numpages
    rows_per_page = len(df) // nh
    cols_per_page = len(df.columns) // nv
    for i in range(0, nh):
        for j in range(0, nv):
            page = df.iloc[(i*rows_per_page):min((i+1)*rows_per_page, len(df)),
                           (j*cols_per_page):min((j+1)*cols_per_page, len(df.columns))]
            fig = _draw_as_table(page, pagesize)
            if nh > 1 or nv > 1:
                # Add a part/page number at bottom-center of page
                fig.text(0.5, 0.5/pagesize[0],
                         "Part-{}x{}: Page-{}".format(i+1, j+1, i*nv + j + 1),
                         ha='center', fontsize=8)
            pdf.savefig(fig, bbox_inches='tight')
            
            plt.close()

In [47]:
### Trying to Align the page number
# https://www.geeksforgeeks.org/matplotlib-figure-figure-text-in-python/
def dataframe_to_pdf(df, filename, numpages=(1, 1), pagesize=(11, 8.5)):
  with PdfPages(filename) as pdf:
    nh, nv = numpages
    rows_per_page = len(df) // nh
    cols_per_page = len(df.columns) // nv
    for i in range(0, nh):
        for j in range(0, nv):
            page = df.iloc[(i*rows_per_page):min((i+1)*rows_per_page, len(df)),
                           (j*cols_per_page):min((j+1)*cols_per_page, len(df.columns))]
            fig = _draw_as_table(page, pagesize)
            #if nh > 1 or nv > 1:
                # Add a part/page number at bottom-center of page
                #fig.text(0.5, 0.5/pagesize[0],
                       # "Part-{}x{}: Page-{}".format(i+1, j+1, i*nv + j + 1),
                       # verticalalignment ='bottom', 
                       # horizontalalignment ='right',
                       #transform = ax.transAxes,
                        #color ='green',
                        #fontsize = 5
                         #)
            pdf.savefig(fig, bbox_inches='tight')
            
            plt.close()

### Creating a pdf file from the divergent data

In [48]:
# dataframe_to_pdf(ts2, "diverge_01.pdf", numpages=(12, 1), pagesize=(11.7, 8.3))

In [49]:
## Create a HTML file of the resumé "ts2" dataframe.

f = open('exp.html','w')
a = ts2.to_html()
f.write(a)
f.close()

In [50]:
# drop the 'confirm" and "total_item_verif" column
transactions = transactions.drop(['confirm'], axis=1)
transactions = transactions.drop(['total_item_verif'], axis=1)


In [51]:
transactions.head()

venda       data     cliente mesa                produto  quantidade  \
0    460 2022-02-01  CONSUMIDOR  M 1  SUCO DE LARANJA 400ML           1   
1    460 2022-02-01  CONSUMIDOR  M 1     PAO SOURDOUGH OVOS           1   
2    461 2022-02-01  CONSUMIDOR  M 2  SUCO DE LARANJA 400ML           1   
3    461 2022-02-01  CONSUMIDOR  M 2     PAO SOURDOUGH OVOS           1   
4    465 2022-02-01  CONSUMIDOR  M 1       QUICHE BACON 90G           2   

   valor_unit  desconto  total_item     horario  hora  minuto hora_minuto  \
0        14.5       0.0        14.5  2022-02-01     8      13    08:13:00   
1        15.5       0.0        15.5  2022-02-01     8      13    08:13:00   
2        14.5       0.0        14.5  2022-02-01     8      14    08:14:00   
3        15.5       0.0        15.5  2022-02-01     8      14    08:14:00   
4        19.5       0.0        39.0  2022-02-01     9       1    09:01:00   

  hora_do_dia dia_da_semana tipo_de_dia  item_count  
0       manhã   terça-feira         DDS           1  
1       manhã   terça-feira         DDS           1  
2       manhã   terça-feira         DDS           1  
3       manhã   terça-feira         DDS           1  
4       manhã   terça-feira         DDS           1

In [52]:
transactions.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 25992 entries, 0 to 25997
Data columns (total 17 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   venda          25992 non-null  int64         
 1   data           25992 non-null  datetime64[ns]
 2   cliente        25992 non-null  object        
 3   mesa           25992 non-null  object        
 4   produto        25992 non-null  object        
 5   quantidade     25992 non-null  int64         
 6   valor_unit     25992 non-null  float64       
 7   desconto       25992 non-null  float64       
 8   total_item     25992 non-null  float64       
 9   horario        25992 non-null  object        
 10  hora           25992 non-null  int64         
 11  minuto         25992 non-null  int64         
 12  hora_minuto    25992 non-null  object        
 13  hora_do_dia    25992 non-null  object        
 14  dia_da_semana  25992 non-null  object        
 15  tipo_de_dia    2599

> # **Exploração dos Dados**

In [53]:
# Find Unique Values of each item sold in the Column "produto"
# https://www.statology.org/pandas-unique-values-in-column/
transactions.produto.value_counts()

CROISSANT                         2393
PASTEL DE NATA 60G                1339
CROISSANT  AMENDOAS 100G           742
FOLHADO MACA 80G                   719
SANDUICHE DE PEPERONI BRIE         596
COOKIES 80G                        559
CROISSANT IFOOD                    534
SOURDOUGH AZEITONA E ALECRIM       517
FOLHADO FRANGO 160G                500
BOMBOLONI DOCE DE LEITE 80G        487
FOCACCIA FORMAGGIO 246G            460
AGUA MINERAL S/GAS 500ML           446
TORRADA FARINA 165G                435
CAFE EQUILIBRADO CAPSULA P         431
SOURDOUGH 369G                     431
LARANJA 400 ML                     430
MINI CROISSANT 25G KIT C 5         427
CROISSANT BRIE PARMA MEL DE        423
PIZZA AL TAGLIO GORGONZOLA E       421
MINI PAIN AU CHOCOLAT 35G          419
BOMBOLONI NUTELLA 80G              409
CROISSANT  TRADICIONAL 80 G        396
QUICHE DE FRANGO ALHO PORO         360
AGUA MINERAL SEM GAS 500 ML        341
COCA COLA LATA 350 ML              337
SUCO DE LARANJA 400ML    

In [54]:
# find the percentage each item is selling
transactions.produto.value_counts(True)

CROISSANT                         0.092067
PASTEL DE NATA 60G                0.051516
CROISSANT  AMENDOAS 100G          0.028547
FOLHADO MACA 80G                  0.027662
SANDUICHE DE PEPERONI BRIE        0.022930
COOKIES 80G                       0.021507
CROISSANT IFOOD                   0.020545
SOURDOUGH AZEITONA E ALECRIM      0.019891
FOLHADO FRANGO 160G               0.019237
BOMBOLONI DOCE DE LEITE 80G       0.018737
FOCACCIA FORMAGGIO 246G           0.017698
AGUA MINERAL S/GAS 500ML          0.017159
TORRADA FARINA 165G               0.016736
CAFE EQUILIBRADO CAPSULA P        0.016582
SOURDOUGH 369G                    0.016582
LARANJA 400 ML                    0.016544
MINI CROISSANT 25G KIT C 5        0.016428
CROISSANT BRIE PARMA MEL DE       0.016274
PIZZA AL TAGLIO GORGONZOLA E      0.016197
MINI PAIN AU CHOCOLAT 35G         0.016120
BOMBOLONI NUTELLA 80G             0.015736
CROISSANT  TRADICIONAL 80 G       0.015235
QUICHE DE FRANGO ALHO PORO        0.013850
AGUA MINERA

In [55]:
## Get unique names in the "produto" column using Series.unique() 
## https://sparkbyexamples.com/pandas/pandas-count-unique-values-in-column/
num_itens_vend = transactions.produto.unique().size

print('O número de diferentes itens vendido pela loja é:', num_itens_vend)

O número de diferentes itens vendido pela loja é: 212


In [56]:
# Look at the average number of items purchased...

avg_items = transactions.groupby(by='venda')['produto'].count().mean()

print('A média de itens por venda é: %.2f itens' %avg_items)

A média de itens por venda é: 2.79 itens


In [57]:
# ...and how that varies by time of day

single_transaction = pd.DataFrame(transactions.groupby(by='venda')['item_count'].sum())

single_transaction = single_transaction.merge(transactions[['hora','minuto','hora_do_dia','data', 'venda']]\
                                              .drop_duplicates('venda'), left_on=single_transaction.index, 
                                              right_on='venda', how='left', copy=False)

print('O número médio de itens vendidos por hora do dia é: \n{0}'.format(
    single_transaction.groupby(by='hora_do_dia')['item_count'].mean()))

O número médio de itens vendidos por hora do dia é: 
hora_do_dia
manhã    3.046419
noite    2.663510
tarde    2.783376
Name: item_count, dtype: float64


In [58]:
# Find the frequency of each item purchased and by time of day

item_frequencies_all = transactions.produto.value_counts()
item_frequencies_morning = transactions[transactions.hora_do_dia == 'manhã'].produto.value_counts()
item_frequencies_afternoon = transactions[transactions.hora_do_dia == 'tarde'].produto.value_counts()
item_frequencies_evening = transactions[transactions.hora_do_dia == 'noite'].produto.value_counts()

In [59]:
# Plot the frequency of purchase for each item

# https://community.plotly.com/t/errors-accessing-plotly-api/33271
# ok, so I found a solution to my problem - when I let my program run through, the error message produced is:
#chart_studio.exceptions.PlotlyRequestError: Authentication credentials were not provided.
#I Googled this error and there were suggestions to run plotly in offline mode by replacing:
#import chart_studio.plotly as py
#with

import plotly.offline as py
#then use py.plot instead of py.iplot

# Solving the problem of the 'plotly' online library with chart_studio
# https://plotly.com/python/getting-started-with-chart-studio/
import plotly.graph_objs as go
#import chart_studio.plotly as py
# import plotly.express as px

button_layer_1_height = 1.12
button_layer_2_height = 1.065

item_threshold_all = 100
item_threshold_other = 20

trace_all = go.Bar(
            x=item_frequencies_all[item_frequencies_all > item_threshold_all].index,
            y=item_frequencies_all[item_frequencies_all > item_threshold_all].values,
            visible=True,
            name='Todo dia'
    )

trace_morning = go.Bar(
            x=item_frequencies_morning[item_frequencies_morning > item_threshold_other].index,
            y=item_frequencies_morning[item_frequencies_morning > item_threshold_other].values,
            visible=False,
            name='Manhã'
    )

trace_afternoon = go.Bar(
            x=item_frequencies_afternoon[item_frequencies_afternoon > item_threshold_other].index,
            y=item_frequencies_afternoon[item_frequencies_afternoon > item_threshold_other].values,
            visible=False,
            name='Tarde'
    )

trace_evening = go.Bar(
            x=item_frequencies_evening[item_frequencies_evening > 10].index,
            y=item_frequencies_evening[item_frequencies_evening > 10].values,
            visible=False,
            name='Noite'
    )

data = [trace_all, trace_morning, trace_afternoon, trace_evening]

updatemenus = list([
    
    dict(
         buttons=list([   
            dict(label = 'Todo dia',
                 method = 'update',
                 args = [{'visible': [True, False, False, False]},
                         {'title': 'Todo Dia'}]),
             
            dict(label = 'Manhã',
                 method = 'update',
                 args = [{'visible': [False, True, False, False]},
                         {'title': 'Manhã'}]),
             
            dict(label = 'Tarde',
                 method = 'update',
                 args = [{'visible': [False, False, True, False]},
                         {'title': 'Tarde'}]),
             
            dict(label = 'Noite',
                 method = 'update',
                 args = [{'visible': [False, False, False, True]},
                         {'title': 'Noite'}])
        ]),
        type='buttons',
        direction = 'right',
        pad = {'r': 10, 't': 10},
        showactive = True,
        x = 0.3,
        xanchor = 'left',
        y = button_layer_1_height,
        yanchor = 'top' )
])
                
layout = dict(title='Vendas Farina por hora do dia', showlegend=False,
              updatemenus=updatemenus)




fig = dict(data=data, layout=layout)
py.iplot(fig, filename='frequencies-bar.html')

# Creating an animated frequencie line 

In [60]:
# Sales trend by date
# https://www.youtube.com/watch?v=Xjm7fOw6gjY
# use reset index for transforming the data in a variable not a index

grouped_by_date = pd.DataFrame(transactions.groupby(by='horario')['item_count'].sum().reset_index())

In [61]:
grouped_by_date.head()

horario  item_count
0  2022-02-01          74
1  2022-02-02          88
2  2022-02-03          81
3  2022-02-04         110
4  2022-02-05         112

In [62]:
from chart_studio.grid_objs import Grid, Column
import plotly.figure_factory as ff

# Create a plot.ly-friendly table for Sales per day

table = ff.create_table(grouped_by_date)
py.iplot(table, filename='Vendas_por_dia_farina.html')



In [63]:
vendas = px.line(grouped_by_date, x = 'horario', y = 'item_count', title = 'Itens vendidos por dia', labels= {'item_count' : 'Quantidade de itens vendidos','data': 'Data'})
py.iplot(vendas, filename='Vendas_line_chart.html')

In [64]:
grouped_by_date.head()


horario  item_count
0  2022-02-01          74
1  2022-02-02          88
2  2022-02-03          81
3  2022-02-04         110
4  2022-02-05         112

In [65]:
# ajustando o gráfio para retirar dois outliers (490 em 2022-07-30 , 2303 em 2022-06-23 ), utilizando-se de filtro com a função 'where'
indice_atip = np.where((grouped_by_date['item_count'] < 400))
linha=grouped_by_date.loc[indice_atip]

In [66]:
# https://towardsdatascience.com/line-chart-animation-with-plotly-on-jupyter-e19c738dc882



#linha=grouped_by_date: usar se precisar demonstrar os dois outliers

trace1 = go.Scatter(x=linha['horario'][:2],
                    y=linha['item_count'][:2],
                    mode='lines',
                    line=dict(width=1.5),
                    fill = 'tozeroy',
                   fillcolor = 'lightblue'
)
frames = [dict(data= [dict(type='scatter',
                           x=linha['horario'][:k+1],
                           y=linha['item_count'][:k+1]),
                     ],
               traces= [0],  
              )for k  in  range(1, len(linha)-1)]
layout = go.Layout(width=1180,
                   height=750,
                   showlegend=False,
                   hovermode='closest',
                   updatemenus=[
                        dict(
                            type='buttons', showactive=False,
                            y=1.06,
                            x=0.12,
                            xanchor='center',
                            yanchor='auto',
                            pad=dict(t=0, r=10),
                            buttons=[dict(label='Play',
                            method='animate',
                            args=[None, 
                                  dict(frame=dict(duration=30, 
                                                  redraw=False),
                                                  transition=dict(duration=0),
                                                  fromcurrent=True,
                                                  mode='immediate')]
                            )]
                        ),
                        
                    ]              
                  )
layout.update(xaxis =dict(range=['2022-02-01', '2022-10-31'], autorange=False),
              yaxis =dict(range=[0, 250], autorange=False)); # ajustar o range se precisar colocar os outliers
fig_vendas = go.Figure(data=[trace1], frames=frames, layout=layout)

fig_vendas.show()

# Investigando dados atipicos

In [67]:
# Vendas atípicas no dia 23 de Junho de 2022 entre 16:00 e 17:00

df_invest = pd.DataFrame(transactions).query("data == 'Jun 23, 2022'").groupby(by='hora')['item_count'].sum().reset_index()
df_invest


hora  item_count
0      7           8
1      9           5
2     10           5
3     11           7
4     12           4
5     13           8
6     14           5
7     15           3
8     16        2254
9     17           3
10    18           1

In [68]:
dataframe_to_pdf(df_invest, "investiga.pdf", numpages=(1, 1), pagesize=(11.7, 8.3))

In [69]:
graf = px.line(df_invest, x = 'hora', y = 'item_count', labels= {'item_count':'Itens Vendidos'}, title= 'Itens vendidos no dia 23 de Junho 2022')

py.iplot(graf, filename='investiga_graf.html')


# Vendas dias de semana (DDS) vs Final de semana (FDS)

In [70]:
dds_vendas= pd.DataFrame(transactions[transactions.tipo_de_dia == 'DDS'].groupby(by='horario')['item_count'].sum())
fds_vendas= pd.DataFrame(transactions[transactions.tipo_de_dia == 'FDS'].groupby(by='horario')['item_count'].sum())

In [71]:
dds_vendas.head()

item_count
horario               
2022-02-01          74
2022-02-02          88
2022-02-03          81
2022-02-04         110
2022-02-07          61

In [72]:
dds_vendas_filter = (dds_vendas['item_count']< 399)

In [73]:
fds_vendas_filter = (fds_vendas['item_count'] < 399)

In [74]:
print('O menor número de vendas em um dia de semana foi: \n{0}'.format(
    dds_vendas.item_count.min()))
print('O número médio de vendas em um dia de semana é: \n{0}'.format(
    dds_vendas.item_count.mean()))
print('O maior número de vendas em um dia de semana foi: \n{0}'.format(
    dds_vendas.item_count.max()))

O menor número de vendas em um dia de semana foi: 
1
O número médio de vendas em um dia de semana é: 
88.18333333333334
O maior número de vendas em um dia de semana foi: 
2303


In [75]:
print('O menor número de vendas em um dia de fim-de-semana foi: \n{0}'.format(
    fds_vendas.item_count.min()))
print('O número médio de vendas em um dia fim-de-semana é: \n{0}'.format(
    fds_vendas.item_count.mean()))
print('O maior número de vendas em um dia fim-de-semana foi: \n{0}'.format(
    fds_vendas.item_count.max()))

O menor número de vendas em um dia de fim-de-semana foi: 
65
O número médio de vendas em um dia fim-de-semana é: 
138.6164383561644
O maior número de vendas em um dia fim-de-semana foi: 
490


In [76]:
single_transaction = pd.DataFrame(transactions.groupby(by='venda')['item_count'].sum())

single_transaction = single_transaction.merge(transactions[['tipo_de_dia','horario', 'venda']]\
                                              .drop_duplicates('venda'), left_on=single_transaction.index, 
                                              right_on='venda', how='left', copy=False)

print('O número médio de itens em cada venda por tipo de dia é: \n{0}'.format(
    single_transaction.groupby(by='tipo_de_dia')['item_count'].mean()))

O número médio de itens em cada venda por tipo de dia é: 
tipo_de_dia
DDS    2.768707
FDS    2.828116
Name: item_count, dtype: float64


In [77]:
# Histogram of items sold by type of day

trace_dds = go.Histogram(
    x=dds_vendas[dds_vendas.item_count < 200].item_count,
    opacity=0.75,
    name = 'Dia de Semana'
)

trace_fds = go.Histogram(
    x=fds_vendas[fds_vendas.item_count < 399].item_count,
    opacity=0.65,
    name = 'Fim-de-semana',
    nbinsx = 16
)

data = [trace_dds, trace_fds]
layout = go.Layout( title = 'Distribuição das vendas por dias de semana/ finais de semana',
                   xaxis=dict(title='Número de Itens Vendidos'),
                   yaxis=dict(title='Frequencia de vendas'),
                   barmode='overlay'
                   )

fig = go.Figure(data=data, layout=layout)

py.iplot(fig, filename='tipo-de_dia-histograma')

# Faturamento por tipo de dia (DDS x FDS)

In [78]:
dds_fatu= pd.DataFrame(transactions[transactions.tipo_de_dia == 'DDS'].groupby(by='horario')['total_item'].sum())
fds_fatu= pd.DataFrame(transactions[transactions.tipo_de_dia == 'FDS'].groupby(by='horario')['total_item'].sum())

In [79]:
# Histograma

trace_dds = go.Histogram(
    x=dds_fatu[dds_fatu.total_item  < 7900].total_item,
    opacity=0.75,
    name = 'Dia de Semana'
)

trace_fds = go.Histogram(
    x=fds_fatu[fds_fatu.total_item < 7900].total_item,
    opacity=0.65,
    name = 'Fim-de-semana',
    nbinsx = 16
)

data = [trace_dds, trace_fds]
layout = go.Layout( title = 'Distribuição do faturamento por dias de semana/ finais de semana',
                   xaxis=dict(title='Faturamento por dia'),
                   yaxis=dict(title='Frequencia de faturamento diário'),
                   barmode='overlay'
                   )

fig = go.Figure(data=data, layout=layout)

py.iplot(fig, filename='tipo-de_dia-histograma')

# Número de itens vendidos por dia da semana

In [80]:
f_filter = (transactions['data']!='2022-06-23')&(transactions['data']!='2022-07-30')
transactions[f_filter]

transactions_filtrada = transactions[f_filter]

In [81]:
grouped_by_date_filtrada = pd.DataFrame(transactions_filtrada.groupby(by='horario')['item_count'].sum())

In [82]:
grouped_by_date_filtrada.head()

item_count
horario               
2022-02-01          74
2022-02-02          88
2022-02-03          81
2022-02-04         110
2022-02-05         112

In [83]:
# Find the number of itens sold per day of week

agregado_vendas_por_dia = grouped_by_date_filtrada.merge(transactions[['dia_da_semana', 'horario']], left_index=True, right_on='horario',
        how= 'left', validate='1:m')



In [84]:
agregado_vendas_por_dia.head()

item_count dia_da_semana     horario
0          74   terça-feira  2022-02-01
1          74   terça-feira  2022-02-01
2          74   terça-feira  2022-02-01
3          74   terça-feira  2022-02-01
4          74   terça-feira  2022-02-01

In [85]:
agregado_vendas_por_dia = agregado_vendas_por_dia[~agregado_vendas_por_dia.index.duplicated(keep='first')]

dias = ['segunda-feira','terça-feira','quarta-feira','quinta-feira','sexta-feira','sábado','domingo']

vendas_por_dia = []

for dia in dias:
    
    df_dias= agregado_vendas_por_dia[agregado_vendas_por_dia.dia_da_semana == dia]
    
    vendas_por_dia.append(list(df_dias['item_count']))

In [86]:
traces = []

for i, j in enumerate(dias):
    
    trace = go.Box(
    y=vendas_por_dia[i],
    name = j
    )
    traces.append(trace)

data = traces

layout = go.Layout(title='Vendas por dia da semana',
                  xaxis = dict(title = 'Dia da Semana'),
                  yaxis = dict(title = 'Número de Itens Vendidos'))

fig = go.Figure(data = data, layout = layout)

py.iplot(fig, filename='Vendas_por_dia_Boxplot')

# Horário de vendas dos itens por dia da semana

In [87]:
dia_hora_df = transactions_filtrada[[ 'hora_minuto','dia_da_semana', 'hora', 'item_count']]


In [88]:
dia_hora_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 23199 entries, 0 to 25997
Data columns (total 4 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   hora_minuto    23199 non-null  object
 1   dia_da_semana  23199 non-null  object
 2   hora           23199 non-null  int64 
 3   item_count     23199 non-null  int64 
dtypes: int64(2), object(2)
memory usage: 906.2+ KB


In [89]:
dia_hora_df.sort_values(['dia_da_semana','hora']).head()


hora_minuto dia_da_semana  hora  item_count
25837    06:38:00       domingo     6           1
25838    06:38:00       domingo     6           1
25839    06:38:00       domingo     6           1
25840    06:51:00       domingo     6           1
465      07:05:00       domingo     7           1

### Modo Simples

In [90]:
dia_hora_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 23199 entries, 0 to 25997
Data columns (total 4 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   hora_minuto    23199 non-null  object
 1   dia_da_semana  23199 non-null  object
 2   hora           23199 non-null  int64 
 3   item_count     23199 non-null  int64 
dtypes: int64(2), object(2)
memory usage: 906.2+ KB


In [91]:
px.box(dia_hora_df, y = 'hora', hover_data=['item_count'])


In [164]:
fig = px.box(dia_hora_df, y = 'hora', x = 'dia_da_semana', color='dia_da_semana', 
title="Hora das vendas dia da semana", hover_data = [dia_hora_df.index])

fig.show()

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



In [165]:
px.box(dia_hora_df, y = 'hora', x = 'dia_da_semana', color='dia_da_semana',title="Hora das vendas dia da semana", )


c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



### Modo Complexo

In [94]:
hora_agrupada_dia = pd.DataFrame(dia_hora_df.groupby(['dia_da_semana','hora'])['item_count'].count()).reset_index()


In [95]:
hora_agrupada_dia.head()

dia_da_semana  hora  item_count
0       domingo     6           4
1       domingo     7         108
2       domingo     8         401
3       domingo     9         557
4       domingo    10         669

In [96]:
horas = [6, 7,8,9,10,11,12,13,14,15,16,17,18,19,20,21]

In [161]:
vendas_hora_por_dia = []

for h in horas:
    
    df_horas_dias= hora_agrupada_dia[hora_agrupada_dia.hora == h]
    
    vendas_hora_por_dia.append(list(df_horas_dias['item_count']))

In [98]:
vendas_hora_por_dia = []

for dia in dias:
    df_horas_dias= hora_agrupada_dia[hora_agrupada_dia.dia_da_semana == dia]
        
    for h in horas:
         df_horas_dias= hora_agrupada_dia[hora_agrupada_dia.hora == h]
    
    vendas_hora_por_dia.append(list(df_horas_dias['item_count']))

In [99]:
vendas_hora_por_dia = []

for dia in dias:
    
    df_horas_dias= hora_agrupada_dia[hora_agrupada_dia.dia_da_semana == dia]
    
    vendas_hora_por_dia.append(list(df_horas_dias['hora']))

In [162]:
vendas_hora_por_dia

[[4, 6, 6, 5, 9, 11],
 [108, 108, 31, 52, 67, 102, 56],
 [401, 128, 115, 131, 154, 278, 82],
 [557, 157, 119, 149, 183, 406, 178],
 [669, 128, 150, 133, 175, 452, 110],
 [571, 115, 111, 116, 160, 265, 108],
 [205, 79, 107, 72, 71, 153, 50],
 [167, 69, 93, 46, 95, 91, 66],
 [105, 165, 98, 65, 69, 175, 92],
 [176, 225, 168, 139, 162, 202, 177],
 [279, 273, 263, 226, 272, 365, 234],
 [579, 342, 461, 344, 519, 547, 487],
 [423, 371, 381, 378, 451, 578, 335],
 [375, 321, 341, 302, 325, 473, 279],
 [369, 321, 239, 271, 268, 406, 220],
 [47, 48, 37, 59, 12, 92, 38]]

In [163]:
traces = []

for i, j in enumerate(dias):
    
    trace = go.Box(
    y=vendas_hora_por_dia[i],
    name = j
    )
    traces.append(trace)

data = traces

layout = go.Layout(title='Hora das vendas dia da semana',
                  xaxis = dict(title = 'Dia da Semana'),
                  yaxis = dict(title = 'Hora de Vendas'))

fig = go.Figure(data = data, layout = layout)

py.iplot(fig, filename='Vendas_hora_por_dia_Boxplot')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\plotly\io\_renderers.py:395: DeprecationWarning:

distutils Version classes are deprecated. Use packaging.version instead.



## Quantidade de itens vendidos por dia da semana e período


In [102]:
group_by_data_e_hora_do_dia = transactions_filtrada.groupby(by=['dia_da_semana','hora_do_dia'])['item_count'].sum()

In [103]:
# https://stackoverflow.com/questions/39275294/sort-by-certain-order-situation-pandas-dataframe-groupby
# #### Alterando a ordem de apresentação dos dias da semana(Seg - Dom), usando a lista 'dias' anteriormente criada

group_by_data_e_hora_do_dia = group_by_data_e_hora_do_dia.reindex(dias, level= 'dia_da_semana')

In [104]:
group_by_data_e_hora_do_dia = pd.DataFrame(group_by_data_e_hora_do_dia).reset_index()

In [105]:
group_by_data_e_hora_do_dia

dia_da_semana hora_do_dia  item_count
0   segunda-feira       manhã         587
1   segunda-feira       noite        1354
2   segunda-feira       tarde         548
3     terça-feira       manhã         545
4     terça-feira       noite        1359
5     terça-feira       tarde         619
6    quarta-feira       manhã         642
7    quarta-feira       noite        1403
8    quarta-feira       tarde         811
9    quinta-feira       manhã         526
10   quinta-feira       noite        1459
11   quinta-feira       tarde         729
12    sexta-feira       manhã         744
13    sexta-feira       noite        1575
14    sexta-feira       tarde         669
15         sábado       manhã        1512
16         sábado       noite        2096
17         sábado       tarde         986
18        domingo       manhã        2310
19        domingo       noite        1793
20        domingo       tarde         932

In [106]:
group_by_data_e_hora_do_dia[group_by_data_e_hora_do_dia.hora_do_dia == 'manhã'].item_count

0      587
3      545
6      642
9      526
12     744
15    1512
18    2310
Name: item_count, dtype: int64

In [107]:
trace_manhã = go.Bar(
    y = group_by_data_e_hora_do_dia[group_by_data_e_hora_do_dia.hora_do_dia == 'manhã'].item_count,
    x = group_by_data_e_hora_do_dia[group_by_data_e_hora_do_dia.hora_do_dia == 'manhã'].dia_da_semana,
    name = "manhã",
    opacity=0.6,
)

trace_tarde = go.Bar(
   y = group_by_data_e_hora_do_dia[group_by_data_e_hora_do_dia.hora_do_dia == 'tarde'].item_count,
    x = group_by_data_e_hora_do_dia[group_by_data_e_hora_do_dia.hora_do_dia == 'tarde'].dia_da_semana,
    name = "tarde",
    opacity=0.6
)

trace_noite = go.Bar(
   y = group_by_data_e_hora_do_dia[group_by_data_e_hora_do_dia.hora_do_dia == 'noite'].item_count,
    x = group_by_data_e_hora_do_dia[group_by_data_e_hora_do_dia.hora_do_dia == 'noite'].dia_da_semana,
    name = "noite",
    opacity=0.6
)

layout = go.Layout(title='Vendas por período e dia da semana',
                  xaxis = dict(title = 'Dia da Semana'),
                  yaxis = dict(title = 'Número de Itens Vendidos'), hovermode= 'x')

data = [trace_manhã, trace_tarde, trace_noite]

fig = go.Figure(data = data, layout = layout)  

py.iplot(fig, filename='vendas-por-dia-periodo')

### Vendas por hora

In [108]:
vendas_por_hora = pd.DataFrame(
                transactions_filtrada[(transactions_filtrada.hora > 1) & 
                (transactions_filtrada.hora < 21)].groupby(by='hora')['item_count'].sum())

In [109]:
vendas_por_hora

item_count
hora            
6             41
7            524
8           1289
9           1749
10          1817
11          1446
12           737
13           627
14           769
15          1249
16          1912
17          3279
18          2917
19          2416
20          2094

In [110]:
trace = go.Scatter(x=list(vendas_por_hora.index),
                   y=list(vendas_por_hora.item_count),
                   fill = 'tozeroy',
                   fillcolor = 'lightblue')

data = [trace]

layout = dict(
    title='Total de volume de vendas por hora',
    yaxis = dict( title = 'Volume de Itens Vendidos'),
    xaxis=dict( title = 'Hora',
        rangeselector=dict(
            buttons=list([
                dict(count = 12,
                     label='Manhã',
                     step='hour',
                     stepmode='backward'),
                dict(count = 8,
                     label='Tarde',
                     step='hour',
                     stepmode='backward'),
                dict(count = 4,
                    label='Noite',
                    step='hour',
                    stepmode='backward'),
                dict(step='all')
            ]),
            visible = True
        ),
        rangeslider=dict(
            visible = True
        )
    )
)

fig = dict(data=data, layout=layout)
py.iplot(fig, filename = 'vendas-por-hora')

# Apriori Algorithm, Method 1

In [111]:
# Create a list of lists that is conducive to the format expected from apyori

list_of_lists = []

for transaction in list(set(transactions_filtrada.venda)):
    
    df = transactions_filtrada[transactions_filtrada.venda == transaction]
    values = df.produto.values
    
    list_of_lists.append(list(values))

In [112]:
# imprting the 'apriori' function from the 'apyori' module
from apyori import apriori

# Create a list of association rules
association_rules = apriori(list_of_lists, min_confidence = 0.2, min_support = 0.005,min_lift = 2, min_length=2)  
association_results = list(association_rules)

In [113]:
print(association_results)

[RelationRecord(items=frozenset({'ADICIONAL DE MUSSARELA', 'ADICIONAL DE PRESUNTO'}), support=0.0061068702290076335, ordered_statistics=[OrderedStatistic(items_base=frozenset({'ADICIONAL DE MUSSARELA'}), items_add=frozenset({'ADICIONAL DE PRESUNTO'}), confidence=0.5416666666666666, lift=70.95833333333333), OrderedStatistic(items_base=frozenset({'ADICIONAL DE PRESUNTO'}), items_add=frozenset({'ADICIONAL DE MUSSARELA'}), confidence=0.8, lift=70.95833333333333)]), RelationRecord(items=frozenset({'ADICIONAL DE MUSSARELA', 'CROISSANT'}), support=0.009395184967704051, ordered_statistics=[OrderedStatistic(items_base=frozenset({'ADICIONAL DE MUSSARELA'}), items_add=frozenset({'CROISSANT'}), confidence=0.8333333333333333, lift=4.038607474862455)]), RelationRecord(items=frozenset({'CROISSANT', 'ADICIONAL DE PRESUNTO'}), support=0.006928948913681738, ordered_statistics=[OrderedStatistic(items_base=frozenset({'ADICIONAL DE PRESUNTO'}), items_add=frozenset({'CROISSANT'}), confidence=0.9076923076923

In [114]:
for item in association_results:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]
    
    print("Rule: " + items[0] + " -> " + items[1])

    #second index of the inner list
    print("Support: " + str(item[1]))

    #third index of the list located at 0th
    #of the third index of the inner list

    print("Confidence: " + str(item[2][0][2]))
    print("Lift: " + str(item[2][0][3]))
    print("=====================================")


Rule: ADICIONAL DE MUSSARELA -> ADICIONAL DE PRESUNTO
Support: 0.0061068702290076335
Confidence: 0.5416666666666666
Lift: 70.95833333333333
Rule: ADICIONAL DE MUSSARELA -> CROISSANT
Support: 0.009395184967704051
Confidence: 0.8333333333333333
Lift: 4.038607474862455
Rule: CROISSANT -> ADICIONAL DE PRESUNTO
Support: 0.006928948913681738
Confidence: 0.9076923076923077
Lift: 4.398975526465566
Rule: AGUA MINERAL S/GAS 500ML -> CROISSANT
Support: 0.01996476805637111
Confidence: 0.4197530864197531
Lift: 2.0342615428936814
Rule: PAO SOURDOUGH OVOS -> BOWL DE IOGURTE FRUTAS AVEIA
Support: 0.007868467410452143
Confidence: 0.24814814814814815
Lift: 9.107678799489145
Rule: CAFE CATUAI VERMELHO C/LEITE G -> CROISSANT
Support: 0.007868467410452143
Confidence: 0.43506493506493504
Lift: 2.1084677985645546
Rule: CAFE CATUAI VERMELHO G 200ML -> CROISSANT
Support: 0.013740458015267175
Confidence: 0.46799999999999997
Lift: 2.2680819578827545
Rule: CAFE COLMEIA C/ LEITE G 200ML -> CROISSANT
Support: 0.005

## Apriori Algorithm, Method 1 - Manhã

In [115]:
manha_filter = (transactions_filtrada['hora_do_dia']=='manhã')
transactions_filtrada_manha = transactions_filtrada[manha_filter]
# Create a list of lists that is conducive to the format expected from apyori


list_of_lists_manha = []

for transaction in list(set(transactions_filtrada_manha.venda)):
    
    df = transactions_filtrada_manha[transactions_filtrada_manha.venda == transaction]
    values = df.produto.values
    
    list_of_lists_manha.append(list(values))

In [116]:
# imprting the 'apriori' function from the 'apyori' module
from apyori import apriori

# Create a list of association rules
association_rules_manha = apriori(list_of_lists_manha, min_confidence = 0.2, min_support = 0.005,min_lift = 3, min_length=3)  
association_results_manha = list(association_rules_manha)

In [117]:
association_results_manha

[RelationRecord(items=frozenset({'ADICIONAL DE MUSSARELA', 'ADICIONAL DE PRESUNTO'}), support=0.009764758100310697, ordered_statistics=[OrderedStatistic(items_base=frozenset({'ADICIONAL DE MUSSARELA'}), items_add=frozenset({'ADICIONAL DE PRESUNTO'}), confidence=0.5945945945945946, lift=40.5945945945946), OrderedStatistic(items_base=frozenset({'ADICIONAL DE PRESUNTO'}), items_add=frozenset({'ADICIONAL DE MUSSARELA'}), confidence=0.6666666666666667, lift=40.594594594594604)]),
 RelationRecord(items=frozenset({'AGUA MINERAL S/GAS 500ML', 'ADICIONAL DE MUSSARELA'}), support=0.005326231691078562, ordered_statistics=[OrderedStatistic(items_base=frozenset({'ADICIONAL DE MUSSARELA'}), items_add=frozenset({'AGUA MINERAL S/GAS 500ML'}), confidence=0.3243243243243244, lift=5.294947121034079)]),
 RelationRecord(items=frozenset({'ADICIONAL DE MUSSARELA', 'CROISSANT'}), support=0.015090989791389259, ordered_statistics=[OrderedStatistic(items_base=frozenset({'ADICIONAL DE MUSSARELA'}), items_add=froz

In [118]:
for item in association_results_manha:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]
    
    print("Rule: " + items[0] + " -> " + items[1])

    #second index of the inner list
    print("Support: " + str(item[1]))

    #third index of the list located at 0th
    #of the third index of the inner list

    print("Confidence: " + str(item[2][0][2]))
    print("Lift: " + str(item[2][0][3]))
    print("=====================================")

Rule: ADICIONAL DE MUSSARELA -> ADICIONAL DE PRESUNTO
Support: 0.009764758100310697
Confidence: 0.5945945945945946
Lift: 40.5945945945946
Rule: AGUA MINERAL S/GAS 500ML -> ADICIONAL DE MUSSARELA
Support: 0.005326231691078562
Confidence: 0.3243243243243244
Lift: 5.294947121034079
Rule: ADICIONAL DE MUSSARELA -> CROISSANT
Support: 0.015090989791389259
Confidence: 0.918918918918919
Lift: 3.344627341396324
Rule: CROISSANT -> ADICIONAL DE PRESUNTO
Support: 0.013315579227696404
Confidence: 0.9090909090909091
Lift: 3.3088559259803203
Rule: CROISSANT BRIE PARMA MEL DE -> AGUA MINERAL SEM GAS 500 ML
Support: 0.007545494895694629
Confidence: 0.2
Lift: 5.006666666666667
Rule: PAO SOURDOUGH OVOS -> BOWL DE IOGURTE FRUTAS AVEIA
Support: 0.024411895250776743
Confidence: 0.2972972972972973
Lift: 3.9170222854433385
Rule: SELECAO DE PAES GELEIA -> BOWL DE IOGURTE FRUTAS AVEIA
Support: 0.010208610741233911
Confidence: 0.2674418604651163
Lift: 3.2570081709616594
Rule: CAFE CATUAI VERMELHO C/LEITE G -> LA

In [119]:
rule_list_manha = []
for item in association_results_manha:
    
    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]

    rule_list_manha.append ( items[0] + " -> " + items[1])

support_list_manha =[]
for item in association_results_manha:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    #items = [x for x in pair]
    

    #second index of the inner list
    support_list_manha.append( str(item[1]))

confidence_list_manha =[]
for item in association_results_manha:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]
    

    #second index of the inner list
    confidence_list_manha.append(str(item[2][0][2]))

lift_list_manha =[]
for item in association_results_manha:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]
    
    
    #second index of the inner list
    lift_list_manha.append(str(item[2][0][3]))

In [120]:
association_results_manha_df=pd.DataFrame(list
(zip(rule_list_manha, support_list_manha, confidence_list_manha, lift_list_manha)), columns=['Rule','Support', 'Confidence', 'Lift'])

In [121]:
association_results_manha_df.sort_values(by=['Support'],ascending=False)

Rule               Support  \
5   PAO SOURDOUGH OVOS -> BOWL DE IOGURTE FRUTAS A...  0.024411895250776743   
2                 ADICIONAL DE MUSSARELA -> CROISSANT  0.015090989791389259   
3                  CROISSANT -> ADICIONAL DE PRESUNTO  0.013315579227696404   
6   SELECAO DE PAES GELEIA -> BOWL DE IOGURTE FRUT...  0.010208610741233911   
0     ADICIONAL DE MUSSARELA -> ADICIONAL DE PRESUNTO  0.009764758100310697   
16                ADICIONAL DE MUSSARELA -> CROISSANT  0.009320905459387484   
10  CROISSANT BRIE PARMA MEL DE -> SUCO DE LARANJA...   0.00887705281846427   
14  SUCO DE LARANJA 400ML -> CROISSANT OVOS BACON MEL  0.008433200177541057   
12            CROISSANT IFOOD -> SOURDOUGH 369G IFOOD  0.008433200177541057   
11        CROISSANT IFOOD -> PASTEL DE NATA 60G IFOOD  0.008433200177541057   
9   CROISSANT BRIE PARMA MEL DE -> CROISSANT OVOS ...  0.007989347536617843   
7    CAFE CATUAI VERMELHO C/LEITE G -> LARANJA 400 ML  0.007989347536617843   
4   CROISSANT BRIE PARMA MEL DE -> AGUA MINERAL SE...  0.007545494895694629   
15  MINI CROISSANT 25G KIT C 5 -> MINI CROISSANT P...  0.007101642254771416   
13   CROISSANT MUSSATRELA DE -> SUCO DE LARANJA 400ML  0.006657789613848202   
17  CAFE CATUAI VERMELHO G 200ML -> AGUA MINERAL S...  0.006657789613848202   
19     LARANJA 400 ML -> CAFE CATUAI VERMELHO G 200ML  0.006657789613848202   
18                        LARANJA 400 ML -> CROISSANT  0.006213936972924989   
22   PASTEL DE NATA 60G -> SANDUICHE DE PEPERONI BRIE  0.006213936972924989   
8                COOKIES 80G IFOOD -> CROISSANT IFOOD  0.005770084332001775   
1   AGUA MINERAL S/GAS 500ML -> ADICIONAL DE MUSSA...  0.005326231691078562   
20  CAFE CATUAI VERMELHO G 200ML -> PAO SOURDOUGH ...  0.005326231691078562   
21               LARANJA 400 ML -> PAO SOURDOUGH OVOS  0.005326231691078562   

             Confidence                Lift  
5    0.2972972972972973  3.9170222854433385  
2     0.918918918918919   3.344627341396324  
3    0.9090909090909091  3.3088559259803203  
6    0.2674418604651163  3.2570081709616594  
0    0.5945945945945946    40.5945945945946  
16   0.5675675675675677  42.624324324324334  
10  0.22222222222222224   6.032128514056224  
14   0.2289156626506024   5.157469879518072  
12              0.59375   7.309938524590163  
11   0.5428571428571428   6.683372365339578  
9                   0.2               4.506  
7   0.23684210526315788   3.629967776584318  
4                   0.2   5.006666666666667  
15   0.2857142857142857   5.646616541353383  
13   0.2459016393442623   6.674896306537625  
17   0.2054794520547945   3.354675402025015  
19   0.2054794520547945   3.149287112105116  
18  0.29166666666666663   4.470238095238095  
22   0.3783783783783784  3.1928332827209234  
8     0.619047619047619   7.621389539422324  
1    0.3243243243243244   5.294947121034079  
20   0.3076923076923077   5.590570719602978  
21   0.3076923076923077    4.71585557299843

# Convert a list to a Dataframe

In [122]:
rule_list = []
for item in association_results:
    
    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]

    rule_list.append ( items[0] + " -> " + items[1])

support_list =[]
for item in association_results:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    #items = [x for x in pair]
    

    #second index of the inner list
    support_list.append( str(item[1]))
confidence_list =[]
for item in association_results:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]
    

    #second index of the inner list
    confidence_list.append(str(item[2][0][2]))
lift_list =[]
for item in association_results:

    # first index of the inner list
    # Contains base item and add item
    pair = item[0] 
    items = [x for x in pair]
    
    
    #second index of the inner list
    lift_list.append(str(item[2][0][3]))

In [123]:
association_results_df=pd.DataFrame(list
(zip(rule_list, support_list, confidence_list, lift_list)), columns=['Rule','Support', 'Confidence', 'Lift'])

In [124]:
association_results_df

Rule                Support  \
0     ADICIONAL DE MUSSARELA -> ADICIONAL DE PRESUNTO  0.0061068702290076335   
1                 ADICIONAL DE MUSSARELA -> CROISSANT   0.009395184967704051   
2                  CROISSANT -> ADICIONAL DE PRESUNTO   0.006928948913681738   
3               AGUA MINERAL S/GAS 500ML -> CROISSANT    0.01996476805637111   
4   PAO SOURDOUGH OVOS -> BOWL DE IOGURTE FRUTAS A...   0.007868467410452143   
5         CAFE CATUAI VERMELHO C/LEITE G -> CROISSANT   0.007868467410452143   
6           CAFE CATUAI VERMELHO G 200ML -> CROISSANT   0.013740458015267175   
7          CAFE COLMEIA C/ LEITE G 200ML -> CROISSANT    0.00551967116852613   
8                   CAFE COLMEIA G 200ML -> CROISSANT   0.007633587786259542   
9                         LARANJA 400 ML -> CROISSANT   0.021374045801526718   
10  CROISSANT BRIE PARMA MEL DE -> SUCO DE LARANJA...   0.005989430416911333   
11        CROISSANT IFOOD -> PASTEL DE NATA 60G IFOOD   0.005167351732237228   
12  MINI CROISSANT 25G KIT C 5 -> MINI CROISSANT P...    0.00540223135642983   
13                ADICIONAL DE MUSSARELA -> CROISSANT   0.005637110980622431   

             Confidence                Lift  
0    0.5416666666666666   70.95833333333333  
1    0.8333333333333333   4.038607474862455  
2    0.9076923076923077   4.398975526465566  
3    0.4197530864197531  2.0342615428936814  
4   0.24814814814814815   9.107678799489145  
5   0.43506493506493504  2.1084677985645546  
6   0.46799999999999997  2.2680819578827545  
7    0.5280898876404494  2.5592973211487915  
8    0.4276315789473684  2.0724433094688917  
9    0.6275862068965518   3.041489215551587  
10   0.2451923076923077   5.394864341085272  
11   0.4356435643564356   9.391151773405188  
12   0.2358974358974359   5.046901172529314  
13                  0.5   72.16101694915254

In [125]:
table_2 = ff.create_table(association_results_df, height_constant=40)
py.iplot(table_2, filename='Apriori_modelo_01.html')

# Resultado inconsistente

In [126]:
def apriori_results(min_confidence=0, min_support=0.005, sort_by_value = 'lift', min_length =None,
                    hora_do_dia=None, dia_da_semana = None, df=transactions_filtrada):
    
    """
    Takes in a data frame, filters it by time of day, calculates the results of the Apriori algorithm,
    and returns a data frame sorted by lift.
    """
    
    from apyori import apriori
    
    if hora_do_dia != None:
        
        df = df[df.hora_do_dia == hora_do_dia]
        
    if dia_da_semana:
        
        df = df[df.tipo_de_dia == dia_da_semana]
        
    list_of_lists = []

    for transaction in list(set(df.venda)):

        df_t = df[df.venda == transaction]
        values = df_t.produto.values

        list_of_lists.append(list(values))

    if min_length is not None:
        
        list_of_lists = [i for i in list_of_lists if len(i) >= min_length]
        
    association_rules = apriori(list_of_lists, min_confidence = min_confidence, min_support = min_support)  
    association_results = list(association_rules)

    item_1 = []
    item_2 = []
    support = []
    confidence = []
    lift = []

    for item in association_results:

        pair = item[0] 
        items = [x for x in pair]
        
        if min_length is not None:
            
            if len(items) < min_length:

                continue

            else:

                item_1.append(items[0])

            #try:

                item_2.append(items[1])

            #except:

            #    item_2.append('None')
            
        else:
            
            item_1.append(items[0])

            try:

                item_2.append(items[1])

            except:

                item_2.append('None')

        support.append(item[1])

        confidence.append(item[2][0][2])
        lift.append(item[2][0][3])

    df_apriori = pd.DataFrame({'item_1':item_1, 'item_2':item_2, 'support':support,'confidence':confidence,'lift':lift})
    
    df_apriori = df_apriori.sort_values(by=sort_by_value, ascending=False)
    
    return df_apriori

In [127]:
all_day_results = apriori_results()

In [128]:
all_day_results[:20]

item_1                        item_2   support  \
0          ABACAXI CURCUMA GENGIBRE                          None  0.007986   
104                       CROISSANT  BOWL DE IOGURTE FRUTAS AVEIA  0.008103   
106  CAFE CATUAI VERMELHO C/LEITE G                     CROISSANT  0.007868   
107    CAFE CATUAI VERMELHO G 200ML                     CROISSANT  0.013740   
108              PASTEL DE NATA 60G  CAFE CATUAI VERMELHO G 200ML  0.005872   
109   CAFE COLMEIA C/ LEITE G 200ML                     CROISSANT  0.005520   
110            CAFE COLMEIA G 200ML                     CROISSANT  0.007634   
111      CAFE EQUILIBRADO CAPSULA G                     CROISSANT  0.005167   
112      CAFE EQUILIBRADO CAPSULA P                     CROISSANT  0.009043   
113      CAFE EQUILIBRADO CAPSULA P            PASTEL DE NATA 60G  0.010570   
114     CAFE INTENSO CAPSULA P 50ML                     CROISSANT  0.005050   
115           COCA COLA LATA 350 ML                     CROISSANT  0.009982   
116              PASTEL DE NATA 60G         COCA COLA LATA 350 ML  0.006107   
117      COCA COLA ZERO LATA 350 ML                     CROISSANT  0.007046   
118                     COOKIES 80G                     CROISSANT  0.012449   
119                     COOKIES 80G      CROISSANT  AMENDOAS 100G  0.006224   
120                     COOKIES 80G              FOLHADO MACA 80G  0.005167   
121                     COOKIES 80G            PASTEL DE NATA 60G  0.010804   
122     COUVE LIMAO ABACAXI HORTELA                     CROISSANT  0.005755   
105              PAO SOURDOUGH OVOS  BOWL DE IOGURTE FRUTAS AVEIA  0.007868   

     confidence  lift  
0      0.007986   1.0  
104    0.008103   1.0  
106    0.007868   1.0  
107    0.013740   1.0  
108    0.005872   1.0  
109    0.005520   1.0  
110    0.007634   1.0  
111    0.005167   1.0  
112    0.009043   1.0  
113    0.010570   1.0  
114    0.005050   1.0  
115    0.009982   1.0  
116    0.006107   1.0  
117    0.007046   1.0  
118    0.012449   1.0  
119    0.006224   1.0  
120    0.005167   1.0  
121    0.010804   1.0  
122    0.005755   1.0  
105    0.007868   1.0

In [129]:
morning_results = apriori_results(hora_do_dia ='manhã')

In [130]:
morning_results[:20]

item_1                      item_2   support  \
0         ABACAXI CURCUMA GENGIBRE                        None  0.009321   
153                    COOKIES 80G                   CROISSANT  0.016866   
142     CAFE EQUILIBRADO CAPSULA G          PAO SOURDOUGH OVOS  0.007102   
143     CAFE EQUILIBRADO CAPSULA P                   CROISSANT  0.011540   
144     CAFE EQUILIBRADO CAPSULA P    CROISSANT OVOS BACON MEL  0.005770   
145     CAFE EQUILIBRADO CAPSULA P          PAO SOURDOUGH OVOS  0.005326   
146     CAFE EQUILIBRADO CAPSULA P          PASTEL DE NATA 60G  0.008433   
147   CAFE INTENSO CAPSULA G 150ML                   CROISSANT  0.009321   
148   CAFE INTENSO CAPSULA G 150ML          PAO SOURDOUGH OVOS  0.005770   
149    CAFE INTENSO CAPSULA P 50ML                   CROISSANT  0.007989   
150    CAFE INTENSO CAPSULA P 50ML          PASTEL DE NATA 60G  0.005326   
151  CAFE ORGANICO CAPSULA G 150ML                   CROISSANT  0.007102   
152     COCA COLA ZERO LATA 350 ML                   CROISSANT  0.005326   
154                    COOKIES 80G          PASTEL DE NATA 60G  0.008877   
140           CAFE COLMEIA G 200ML                   CROISSANT  0.016866   
155                    COOKIES 80G  SANDUICHE DE PEPERONI BRIE  0.005326   
156                    COOKIES 80G         TORRADA FARINA 165G  0.006658   
157              COOKIES 80G IFOOD             CROISSANT IFOOD  0.005770   
158                      CROISSANT  COUVE ABACAXI AGUA DE COCO  0.007989   
159    COUVE LIMAO ABACAXI HORTELA                   CROISSANT  0.010652   

     confidence  lift  
0      0.009321   1.0  
153    0.016866   1.0  
142    0.007102   1.0  
143    0.011540   1.0  
144    0.005770   1.0  
145    0.005326   1.0  
146    0.008433   1.0  
147    0.009321   1.0  
148    0.005770   1.0  
149    0.007989   1.0  
150    0.005326   1.0  
151    0.007102   1.0  
152    0.005326   1.0  
154    0.008877   1.0  
140    0.016866   1.0  
155    0.005326   1.0  
156    0.006658   1.0  
157    0.005770   1.0  
158    0.007989   1.0  
159    0.010652   1.0

In [131]:
afternoon_results = apriori_results(hora_do_dia ='tarde')

In [132]:
afternoon_results[:20]

item_1                        item_2   support  \
0       ABACAXI CURCUMA GENGIBRE                          None  0.011337   
1         ADICIONAL DE MUSSARELA                          None  0.010392   
102   CAFE EQUILIBRADO CAPSULA G            PASTEL DE NATA 60G  0.005668   
103   CAFE EQUILIBRADO CAPSULA P   CAFE INTENSO CAPSULA P 50ML  0.007085   
104   CAFE EQUILIBRADO CAPSULA P                     CROISSANT  0.007558   
105   CAFE EQUILIBRADO CAPSULA P            PASTEL DE NATA 60G  0.014643   
106  CAFE INTENSO CAPSULA P 50ML                     CROISSANT  0.005668   
107  CAFE INTENSO CAPSULA P 50ML            PASTEL DE NATA 60G  0.007085   
108        COCA COLA LATA 350 ML                     CROISSANT  0.011809   
109        COCA COLA LATA 350 ML           FOLHADO FRANGO 160G  0.005196   
110           PASTEL DE NATA 60G         COCA COLA LATA 350 ML  0.005196   
111   COCA COLA ZERO LATA 350 ML                     CROISSANT  0.005196   
112                  COOKIES 80G                     CROISSANT  0.013699   
113                  COOKIES 80G      CROISSANT  AMENDOAS 100G  0.005668   
114                  COOKIES 80G       FOCACCIA FORMAGGIO 246G  0.005668   
115                  COOKIES 80G              FOLHADO MACA 80G  0.005668   
116                  COOKIES 80G    MINI CROISSANT 25G KIT C 5  0.005196   
117                  COOKIES 80G            PASTEL DE NATA 60G  0.013226   
118                  COOKIES 80G  SOURDOUGH AZEITONA E ALECRIM  0.005196   
101        BOMBOLONI NUTELLA 80G            PASTEL DE NATA 60G  0.007085   

     confidence  lift  
0      0.011337   1.0  
1      0.010392   1.0  
102    0.005668   1.0  
103    0.007085   1.0  
104    0.007558   1.0  
105    0.014643   1.0  
106    0.005668   1.0  
107    0.007085   1.0  
108    0.011809   1.0  
109    0.005196   1.0  
110    0.005196   1.0  
111    0.005196   1.0  
112    0.013699   1.0  
113    0.005668   1.0  
114    0.005668   1.0  
115    0.005668   1.0  
116    0.005196   1.0  
117    0.013226   1.0  
118    0.005196   1.0  
101    0.007085   1.0

In [133]:
evening_results = apriori_results(hora_do_dia='noite')

In [134]:
evening_results[:20]

item_1                        item_2   support  \
0       ABACAXI CURCUMA GENGIBRE                          None  0.005549   
122          FOLHADO FRANGO 160G                     CROISSANT  0.012545   
104   CAFE EQUILIBRADO CAPSULA P            PASTEL DE NATA 60G  0.009650   
105        COCA COLA LATA 350 ML                     CROISSANT  0.012063   
106  CROISSANT BRIE PARMA MEL DE         COCA COLA LATA 350 ML  0.005549   
107        COCA COLA LATA 350 ML           FOLHADO FRANGO 160G  0.005790   
108        COCA COLA LATA 350 ML              FOLHADO MACA 80G  0.007238   
109           PASTEL DE NATA 60G         COCA COLA LATA 350 ML  0.009168   
110        COCA COLA LATA 350 ML  PIZZA AL TAGLIO GORGONZOLA E  0.006996   
111        COCA COLA LATA 350 ML    SANDUICHE DE PEPERONI BRIE  0.005066   
112   COCA COLA ZERO LATA 350 ML                     CROISSANT  0.008926   
113           PASTEL DE NATA 60G    COCA COLA ZERO LATA 350 ML  0.006514   
114   COCA COLA ZERO LATA 350 ML    SANDUICHE DE PEPERONI BRIE  0.006031   
115                  COOKIES 80G                     CROISSANT  0.009409   
116                  COOKIES 80G      CROISSANT  AMENDOAS 100G  0.007720   
117                  COOKIES 80G           FOLHADO FRANGO 160G  0.005308   
118                  COOKIES 80G              FOLHADO MACA 80G  0.005308   
119                  COOKIES 80G            PASTEL DE NATA 60G  0.010615   
120     CROISSANT  AMENDOAS 100G                     CROISSANT  0.018094   
103   CAFE EQUILIBRADO CAPSULA P              FOLHADO MACA 80G  0.005066   

     confidence  lift  
0      0.005549   1.0  
122    0.012545   1.0  
104    0.009650   1.0  
105    0.012063   1.0  
106    0.005549   1.0  
107    0.005790   1.0  
108    0.007238   1.0  
109    0.009168   1.0  
110    0.006996   1.0  
111    0.005066   1.0  
112    0.008926   1.0  
113    0.006514   1.0  
114    0.006031   1.0  
115    0.009409   1.0  
116    0.007720   1.0  
117    0.005308   1.0  
118    0.005308   1.0  
119    0.010615   1.0  
120    0.018094   1.0  
103    0.005066   1.0

In [135]:
weekday_results = apriori_results(dia_da_semana= 'DDS')

In [136]:
weekday_results[:20]

item_1                        item_2   support  \
0          ABACAXI CURCUMA GENGIBRE                          None  0.007812   
94      BOMBOLONI DOCE DE LEITE 80G                     CROISSANT  0.007422   
96            BOMBOLONI NUTELLA 80G                     CROISSANT  0.009570   
97            BOMBOLONI NUTELLA 80G           FOLHADO FRANGO 160G  0.005469   
98            BOMBOLONI NUTELLA 80G            PASTEL DE NATA 60G  0.007227   
99               PAO SOURDOUGH OVOS  BOWL DE IOGURTE FRUTAS AVEIA  0.006836   
100  CAFE CATUAI VERMELHO C/LEITE G                     CROISSANT  0.006055   
101    CAFE CATUAI VERMELHO G 200ML                     CROISSANT  0.011914   
102   CAFE COLMEIA C/ LEITE G 200ML                     CROISSANT  0.005859   
103            CAFE COLMEIA G 200ML                     CROISSANT  0.008789   
104      CAFE EQUILIBRADO CAPSULA P                     CROISSANT  0.007617   
105      CAFE EQUILIBRADO CAPSULA P            PASTEL DE NATA 60G  0.009961   
106    CAFE INTENSO CAPSULA G 150ML                     CROISSANT  0.005078   
107     CAFE INTENSO CAPSULA P 50ML                     CROISSANT  0.005078   
108           COCA COLA LATA 350 ML                     CROISSANT  0.009961   
109              PASTEL DE NATA 60G         COCA COLA LATA 350 ML  0.005469   
110           COCA COLA LATA 350 ML  PIZZA AL TAGLIO GORGONZOLA E  0.005664   
95               PASTEL DE NATA 60G   BOMBOLONI DOCE DE LEITE 80G  0.007617   
93            BOMBOLONI NUTELLA 80G   BOMBOLONI DOCE DE LEITE 80G  0.007227   
112                     COOKIES 80G                     CROISSANT  0.012109   

     confidence  lift  
0      0.007812   1.0  
94     0.007422   1.0  
96     0.009570   1.0  
97     0.005469   1.0  
98     0.007227   1.0  
99     0.006836   1.0  
100    0.006055   1.0  
101    0.011914   1.0  
102    0.005859   1.0  
103    0.008789   1.0  
104    0.007617   1.0  
105    0.009961   1.0  
106    0.005078   1.0  
107    0.005078   1.0  
108    0.009961   1.0  
109    0.005469   1.0  
110    0.005664   1.0  
95     0.007617   1.0  
93     0.007227   1.0  
112    0.012109   1.0

In [137]:
weekend_results = apriori_results(dia_da_semana = 'FDS')

In [138]:
weekend_results[:20]

item_1                      item_2   support  \
0       ABACAXI CURCUMA GENGIBRE                        None  0.008247   
131                  COOKIES 80G    CROISSANT  AMENDOAS 100G  0.006186   
122   CAFE EQUILIBRADO CAPSULA P                   CROISSANT  0.011193   
123   CAFE EQUILIBRADO CAPSULA P    CROISSANT  AMENDOAS 100G  0.005302   
124   CAFE EQUILIBRADO CAPSULA P          PASTEL DE NATA 60G  0.011487   
125  CAFE INTENSO CAPSULA P 50ML                   CROISSANT  0.005007   
126  CAFE INTENSO CAPSULA P 50ML          PASTEL DE NATA 60G  0.005007   
127        COCA COLA LATA 350 ML                   CROISSANT  0.010015   
128           PASTEL DE NATA 60G       COCA COLA LATA 350 ML  0.007069   
129   COCA COLA ZERO LATA 350 ML                   CROISSANT  0.008542   
130                  COOKIES 80G                   CROISSANT  0.012960   
132                  COOKIES 80G         FOLHADO FRANGO 160G  0.005302   
120   CAFE EQUILIBRADO CAPSULA G          PASTEL DE NATA 60G  0.005007   
133                  COOKIES 80G            FOLHADO MACA 80G  0.006775   
134                  COOKIES 80G          PASTEL DE NATA 60G  0.010015   
135                  COOKIES 80G  SANDUICHE DE PEPERONI BRIE  0.006775   
136                  COOKIES 80G         TORRADA FARINA 165G  0.006775   
137                    CROISSANT  COUVE ABACAXI AGUA DE COCO  0.006186   
138  COUVE LIMAO ABACAXI HORTELA                   CROISSANT  0.009720   
139     CROISSANT  AMENDOAS 100G                   CROISSANT  0.018851   

     confidence  lift  
0      0.008247   1.0  
131    0.006186   1.0  
122    0.011193   1.0  
123    0.005302   1.0  
124    0.011487   1.0  
125    0.005007   1.0  
126    0.005007   1.0  
127    0.010015   1.0  
128    0.007069   1.0  
129    0.008542   1.0  
130    0.012960   1.0  
132    0.005302   1.0  
120    0.005007   1.0  
133    0.006775   1.0  
134    0.010015   1.0  
135    0.006775   1.0  
136    0.006775   1.0  
137    0.006186   1.0  
138    0.009720   1.0  
139    0.018851   1.0

In [139]:
weekday_morning_results = apriori_results(dia_da_semana = 'DDS', hora_do_dia = 'manhã')

In [140]:
weekday_morning_results[:20]

item_1                        item_2   support  \
0         ABACAXI CURCUMA GENGIBRE                          None  0.009506   
148    CAFE INTENSO CAPSULA P 50ML      CROISSANT OVOS BACON MEL  0.005703   
137     CAFE EQUILIBRADO CAPSULA G            PAO SOURDOUGH OVOS  0.009506   
138     CAFE EQUILIBRADO CAPSULA G            PASTEL DE NATA 60G  0.005703   
139     CAFE EQUILIBRADO CAPSULA P   CAFE INTENSO CAPSULA P 50ML  0.005703   
140     CAFE EQUILIBRADO CAPSULA P                     CROISSANT  0.014259   
141     CAFE EQUILIBRADO CAPSULA P      CROISSANT OVOS BACON MEL  0.007605   
142     CAFE EQUILIBRADO CAPSULA P           FOLHADO FRANGO 160G  0.005703   
143     CAFE EQUILIBRADO CAPSULA P            PASTEL DE NATA 60G  0.009506   
144   CAFE INTENSO CAPSULA G 150ML                     CROISSANT  0.013308   
145   CAFE INTENSO CAPSULA G 150ML            PAO SOURDOUGH OVOS  0.006654   
146             PASTEL DE NATA 60G  CAFE INTENSO CAPSULA G 150ML  0.006654   
147    CAFE INTENSO CAPSULA P 50ML                     CROISSANT  0.008555   
149  CAFE ORGANICO CAPSULA G 150ML                     CROISSANT  0.006654   
1           ABACAXI HORTELA 400 ML                          None  0.008555   
150  CAFE ORGANICO CAPSULA G 150ML              FOLHADO MACA 80G  0.005703   
151  CAFE ORGANICO CAPSULA G 150ML        SELECAO DE PAES GELEIA  0.005703   
152          COCA COLA LATA 350 ML                     CROISSANT  0.006654   
153          COCA COLA LATA 350 ML  PIZZA AL TAGLIO GORGONZOLA E  0.005703   
154                    COOKIES 80G                     CROISSANT  0.015209   

     confidence  lift  
0      0.009506   1.0  
148    0.005703   1.0  
137    0.009506   1.0  
138    0.005703   1.0  
139    0.005703   1.0  
140    0.014259   1.0  
141    0.007605   1.0  
142    0.005703   1.0  
143    0.009506   1.0  
144    0.013308   1.0  
145    0.006654   1.0  
146    0.006654   1.0  
147    0.008555   1.0  
149    0.006654   1.0  
1      0.008555   1.0  
150    0.005703   1.0  
151    0.005703   1.0  
152    0.006654   1.0  
153    0.005703   1.0  
154    0.015209   1.0

In [141]:
weekday_afternoon_results = apriori_results(dia_da_semana = 'DDS', hora_do_dia = 'tarde')

In [142]:
weekday_afternoon_results[:20]

item_1                        item_2   support  \
0       ABACAXI CURCUMA GENGIBRE                          None  0.011021   
119                  COOKIES 80G           FOLHADO FRANGO 160G  0.005143   
111        COCA COLA LATA 350 ML                     CROISSANT  0.011756   
112        COCA COLA LATA 350 ML           FOLHADO FRANGO 160G  0.005143   
113           PASTEL DE NATA 60G         COCA COLA LATA 350 ML  0.005878   
114        COCA COLA LATA 350 ML    SANDUICHE DE PEPERONI BRIE  0.007348   
115                  COOKIES 80G                     CROISSANT  0.016899   
116                  COOKIES 80G      CROISSANT  AMENDOAS 100G  0.005143   
117                  COOKIES 80G   CROISSANT  TRADICIONAL 80 G  0.005143   
118                  COOKIES 80G       FOCACCIA FORMAGGIO 246G  0.006613   
120                  COOKIES 80G    MINI CROISSANT 25G KIT C 5  0.005878   
109  CAFE INTENSO CAPSULA P 50ML   CROISSANT  TRADICIONAL 80 G  0.005143   
121                  COOKIES 80G            PASTEL DE NATA 60G  0.015430   
122                  COOKIES 80G  QUICHE DE TOMATE SECO SALADA  0.005143   
123                  COOKIES 80G                SOURDOUGH 369G  0.005143   
124                  COOKIES 80G  SOURDOUGH AZEITONA E ALECRIM  0.006613   
125           PASTEL DE NATA 60G  CROISANT DE CROISSANT QUEIJO  0.005143   
126     CROISSANT  AMENDOAS 100G                     CROISSANT  0.011756   
127      FOCACCIA FORMAGGIO 246G                     CROISSANT  0.005878   
128          FOLHADO FRANGO 160G                     CROISSANT  0.013960   

     confidence  lift  
0      0.011021   1.0  
119    0.005143   1.0  
111    0.011756   1.0  
112    0.005143   1.0  
113    0.005878   1.0  
114    0.007348   1.0  
115    0.016899   1.0  
116    0.005143   1.0  
117    0.005143   1.0  
118    0.006613   1.0  
120    0.005878   1.0  
109    0.005143   1.0  
121    0.015430   1.0  
122    0.005143   1.0  
123    0.005143   1.0  
124    0.006613   1.0  
125    0.005143   1.0  
126    0.011756   1.0  
127    0.005878   1.0  
128    0.013960   1.0

# Apriori Algorithm, Method 2

In [143]:
def apriori_results_method_2(df = transactions_filtrada, min_support = 0.005, hora_do_dia = None, dia_da_semana = None,
                            min_threshold = 1, metric = 'lift'):
    
    """
    Takes in a data frame and returns the results of the Apriori algorithm using the mlxtend Python package.
    """
    
    from mlxtend.frequent_patterns import apriori
    from mlxtend.frequent_patterns import association_rules

    if hora_do_dia:
        
        df = df[df.hora_do_dia == hora_do_dia]
        
    if dia_da_semana:
        
        df = df[df.tipo_de_dia == dia_da_semana]
        
    dummies_df = df.groupby(['venda', 'produto'])['produto'].count().unstack().\
                 reset_index().fillna(0).set_index('venda')
    
    def encode_units(x):
    
        if x <= 0:
            return 0
        if x >= 1:
            return 1
    
    dummies_df = dummies_df.applymap(encode_units)
    
    frequent_itemsets = apriori(dummies_df, min_support= min_support, use_colnames=True)

    rules = association_rules(frequent_itemsets, metric=metric, min_threshold=min_threshold)
    
    rules.drop_duplicates(subset='leverage', keep='first', inplace=True)
    rules = rules.sort_values(by='lift', ascending=False)
    
    return rules

In [144]:
all_day_method_2 = apriori_results_method_2()

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [145]:
all_day_method_2[:20]

antecedents  \
114              (ADICIONAL DE MUSSARELA, CROISSANT)   
116               (CROISSANT, ADICIONAL DE PRESUNTO)   
0                           (ADICIONAL DE MUSSARELA)   
86                                 (CROISSANT IFOOD)   
30                              (PAO SOURDOUGH OVOS)   
82                     (CROISSANT BRIE PARMA MEL DE)   
96                      (MINI CROISSANT 25G KIT C 5)   
115  (ADICIONAL DE MUSSARELA, ADICIONAL DE PRESUNTO)   
4                                        (CROISSANT)   
2                           (ADICIONAL DE MUSSARELA)   
12                     (CROISSANT BRIE PARMA MEL DE)   
16                           (BOMBOLONI NUTELLA 80G)   
78                     (CROISSANT BRIE PARMA MEL DE)   
66                                  (LARANJA 400 ML)   
84                       (MINI PAIN AU CHOCOLAT 35G)   
38                   (CAFE COLMEIA C/ LEITE G 200ML)   
24                           (BOMBOLONI NUTELLA 80G)   
34                    (CAFE CATUAI VERMELHO G 200ML)   
88                    (SOURDOUGH AZEITONA E ALECRIM)   
32                  (CAFE CATUAI VERMELHO C/LEITE G)   

                        consequents  antecedent support  consequent support  \
114         (ADICIONAL DE PRESUNTO)            0.009395            0.007634   
116        (ADICIONAL DE MUSSARELA)            0.006929            0.011274   
0           (ADICIONAL DE PRESUNTO)            0.011274            0.007634   
86       (PASTEL DE NATA 60G IFOOD)            0.046389            0.011861   
30   (BOWL DE IOGURTE FRUTAS AVEIA)            0.027246            0.031709   
82          (SUCO DE LARANJA 400ML)            0.045449            0.024427   
96    (MINI CROISSANT PAIN DE CHOC)            0.046741            0.022901   
115                     (CROISSANT)            0.006107            0.206342   
4           (ADICIONAL DE PRESUNTO)            0.206342            0.007634   
2                       (CROISSANT)            0.011274            0.206342   
12    (AGUA MINERAL SEM GAS 500 ML)            0.045449            0.036054   
16    (BOMBOLONI DOCE DE LEITE 80G)            0.044157            0.052496   
78        (CROISSANT MUSSATRELA DE)            0.045449            0.031826   
66                      (CROISSANT)            0.034058            0.206342   
84                (CROISSANT IFOOD)            0.044862            0.046389   
38                      (CROISSANT)            0.010452            0.206342   
24            (FOLHADO FRANGO 160G)            0.044157            0.052378   
34                      (CROISSANT)            0.029360            0.206342   
88        (FOCACCIA FORMAGGIO 246G)            0.056841            0.049560   
32                      (CROISSANT)            0.018086            0.206342   

      support  confidence       lift  leverage  conviction  
114  0.005637    0.600000  78.600000  0.005565    2.480916  
116  0.005637    0.813559  72.161017  0.005559    5.303166  
0    0.006107    0.541667  70.958333  0.006021    2.165163  
86   0.005167    0.111392   9.391152  0.004617    1.112008  
30   0.007868    0.288793   9.107679  0.007005    1.361476  
82   0.005989    0.131783   5.394864  0.004879    1.123650  
96   0.005402    0.115578   5.046901  0.004332    1.104788  
115  0.005637    0.923077   4.473534  0.004377   10.317557  
4    0.006929    0.033580   4.398976  0.005354    1.026848  
2    0.009395    0.833333   4.038607  0.007069    4.761950  
12   0.006107    0.134367   3.726822  0.004468    1.113573  
16   0.008103    0.183511   3.495734  0.005785    1.160461  
78   0.005050    0.111111   3.491185  0.003603    1.089196  
66   0.021374    0.627586   3.041489  0.014347    2.131119  
84   0.005402    0.120419   2.595865  0.003321    1.084165  
38   0.005520    0.528090   2.559297  0.003363    1.681800  
24   0.005402    0.122340   2.335715  0.003089    1.079715  
34   0.013740    0.468000   2.268082  0.007682    1.491839  
88   0.006342    0.111570   2.251234  0.00352

In [146]:
morning_method_2 = apriori_results_method_2(hora_do_dia = 'manhã')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [147]:
morning_method_2[:20]

antecedents  \
218         (CROISSANT, ADICIONAL DE PRESUNTO)   
216        (ADICIONAL DE MUSSARELA, CROISSANT)   
0                     (ADICIONAL DE MUSSARELA)   
132                        (COOKIES 80G IFOOD)   
176                          (CROISSANT IFOOD)   
174                          (CROISSANT IFOOD)   
178                  (CROISSANT MUSSATRELA DE)   
170              (CROISSANT BRIE PARMA MEL DE)   
196               (MINI CROISSANT 25G KIT C 5)   
248            (PAO SOURDOUGH OVOS, CROISSANT)   
2                   (AGUA MINERAL S/GAS 500ML)   
38                   (CROISSANT MUSSATRELA DE)   
182                    (SUCO DE LARANJA 400ML)   
36               (CROISSANT BRIE PARMA MEL DE)   
254            (PAO SOURDOUGH OVOS, CROISSANT)   
166              (CROISSANT BRIE PARMA MEL DE)   
236  (CROISSANT, BOWL DE IOGURTE FRUTAS AVEIA)   
46                     (BOMBOLONI NUTELLA 80G)   
40                  (CROISSANT OVOS BACON MEL)   
72                        (PAO SOURDOUGH OVOS)   

                        consequents  antecedent support  consequent support  \
218        (ADICIONAL DE MUSSARELA)            0.013316            0.016423   
216         (ADICIONAL DE PRESUNTO)            0.015091            0.014647   
0           (ADICIONAL DE PRESUNTO)            0.016423            0.014647   
132               (CROISSANT IFOOD)            0.009321            0.081225   
176          (SOURDOUGH 369G IFOOD)            0.081225            0.014203   
174      (PASTEL DE NATA 60G IFOOD)            0.081225            0.015535   
178         (SUCO DE LARANJA 400ML)            0.027075            0.036840   
170         (SUCO DE LARANJA 400ML)            0.039947            0.036840   
196   (MINI CROISSANT PAIN DE CHOC)            0.050599            0.024856   
248  (CAFE CATUAI VERMELHO G 200ML)            0.017310            0.055038   
2          (ADICIONAL DE MUSSARELA)            0.061252            0.016423   
38    (AGUA MINERAL SEM GAS 500 ML)            0.027075            0.037727   
182      (CROISSANT OVOS BACON MEL)            0.036840            0.044385   
36    (AGUA MINERAL SEM GAS 500 ML)            0.039947            0.037727   
254                (LARANJA 400 ML)            0.017310            0.065246   
166      (CROISSANT OVOS BACON MEL)            0.039947            0.044385   
236                (LARANJA 400 ML)            0.021305            0.065246   
46    (BOMBOLONI DOCE DE LEITE 80G)            0.036840            0.038171   
40    (AGUA MINERAL SEM GAS 500 ML)            0.044385            0.037727   
72   (BOWL DE IOGURTE FRUTAS AVEIA)            0.075899            0.082113   

      support  confidence       lift  leverage  conviction  
218  0.009321    0.700000  42.624324  0.009102    3.278592  
216  0.009321    0.617647  42.168449  0.009100    2.577077  
0    0.009765    0.594595  40.594595  0.009524    2.430537  
132  0.005770    0.619048   7.621390  0.005013    2.411784  
176  0.008433    0.103825   7.309939  0.007280    1.100005  
174  0.008433    0.103825   6.683372  0.007171    1.098519  
178  0.006658    0.245902   6.674896  0.005660    1.277234  
170  0.008877    0.222222   6.032129  0.007405    1.238349  
196  0.007102    0.140351   5.646617  0.005844    1.134351  
248  0.005326    0.307692   5.590571  0.004374    1.364946  
2    0.005326    0.086957   5.294947  0.004320    1.077251  
38   0.005326    0.196721   5.214272  0.004305    1.197931  
182  0.008433    0.228916   5.157470  0.006798    1.239313  
36   0.007545    0.188889   5.006667  0.006038    1.186363  
254  0.005326    0.307692   4.715856  0.004197    1.350200  
166  0.007989    0.200000   4.506000  0.006216    1.194518  
236  0.006214    0.291667   4.470238  0.004824    1.319652  
46   0.006214    0.168675   4.418885  0.004808    1.156982  
40   0.007102    0.160000   4.240941  0.005427    1.145563  
72   0.024412    0.321637   3.917022  0.018180    1.353092

In [148]:
afternoon_method_2 = apriori_results_method_2(hora_do_dia = 'tarde')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [149]:
afternoon_method_2[:20]

antecedents                     consequents  \
118  (ADICIONAL DE MUSSARELA, CROISSANT)         (ADICIONAL DE PRESUNTO)   
0               (ADICIONAL DE MUSSARELA)         (ADICIONAL DE PRESUNTO)   
120   (CROISSANT, ADICIONAL DE PRESUNTO)        (ADICIONAL DE MUSSARELA)   
84                     (CROISSANT IFOOD)      (PASTEL DE NATA 60G IFOOD)   
4                            (CROISSANT)         (ADICIONAL DE PRESUNTO)   
32          (CAFE EQUILIBRADO CAPSULA P)   (CAFE INTENSO CAPSULA P 50ML)   
2               (ADICIONAL DE MUSSARELA)                     (CROISSANT)   
96          (MINI CROISSANT 25G KIT C 5)   (MINI CROISSANT PAIN DE CHOC)   
12               (BOMBOLONI NUTELLA 80G)   (BOMBOLONI DOCE DE LEITE 80G)   
64                      (LARANJA 400 ML)                     (CROISSANT)   
14         (BOMBOLONI DOCE DE LEITE 80G)         (COCA COLA LATA 350 ML)   
82           (MINI PAIN AU CHOCOLAT 35G)               (CROISSANT IFOOD)   
116            (SOURDOUGH GERGELIM 370G)  (SOURDOUGH AZEITONA E ALECRIM)   
20               (BOMBOLONI NUTELLA 80G)         (COCA COLA LATA 350 ML)   
44               (COCA COLA LATA 350 ML)           (FOLHADO FRANGO 160G)   
86        (SOURDOUGH AZEITONA E ALECRIM)       (FOCACCIA FORMAGGIO 246G)   
114       (SOURDOUGH AZEITONA E ALECRIM)                (SOURDOUGH 369G)   
26               (BOMBOLONI NUTELLA 80G)           (FOLHADO FRANGO 160G)   
6             (AGUA MINERAL C/GAS 500ML)                     (CROISSANT)   
36          (CAFE EQUILIBRADO CAPSULA P)            (PASTEL DE NATA 60G)   

     antecedent support  consequent support   support  confidence        lift  \
118            0.008975            0.007085  0.006613    0.736842  103.992982   
0              0.010392            0.007085  0.007085    0.681818   96.227273   
120            0.006613            0.010392  0.006613    1.000000   96.227273   
84             0.045820            0.011809  0.005196    0.113402    9.602887   
4              0.168162            0.007085  0.006613    0.039326    5.550187   
32             0.042985            0.030704  0.007085    0.164835    5.368555   
2              0.010392            0.168162  0.008975    0.863636    5.135725   
96             0.053377            0.032121  0.008030    0.150442    4.683628   
12             0.048181            0.059046  0.012754    0.264706    4.483059   
64             0.028342            0.168162  0.017005    0.600000    3.567978   
14             0.059046            0.036372  0.007085    0.120000    3.299221   
82             0.038262            0.045820  0.005668    0.148148    3.233295   
116            0.025508            0.068021  0.005196    0.203704    2.994727   
20             0.048181            0.036372  0.005196    0.107843    2.964986   
44             0.036372            0.050071  0.005196    0.142857    2.853100   
86             0.068021            0.043930  0.008030    0.118056    2.687351   
114            0.068021            0.056212  0.009920    0.145833    2.594363   
26             0.048181            0.050071  0.005668    0.117647    2.349612   
6              0.019839            0.168162  0.007558    0.380952    2.265383   
36             0.042985            0.152102  0.014643    0.340659    2.239676   

     leverage  conviction  
118  0.006550    3.773075  
0    0.007012    3.120588  
120  0.006544         inf  
84   0.004655    1.114587  
4    0.005422    1.033560  
32   0.005766    1.160605  
2    0.007227    6.100142  
96   0.006316    1.139274  
12   0.009909    1.279698  
64   0.012239    2.079594  
14   0.004938    1.095032  
82   0.003915    1.120125  
116  0.003461    1.170393  
20   0.003444    1.080110  
44   0.003375    1.108251  
86   0.005042    1.084048  
114  0.006096    1.104923  
26   0.003256    1.076586  
6    0.004222    1.343738  
36   0.008105    1.285979

In [150]:
evening_method_2 = apriori_results_method_2(hora_do_dia = 'noite')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [151]:
evening_method_2

antecedents                     consequents  \
92      (CROISSANT BRIE PARMA MEL DE)         (SUCO DE LARANJA 400ML)   
0            (ADICIONAL DE MUSSARELA)                     (CROISSANT)   
12      (CROISSANT BRIE PARMA MEL DE)   (AGUA MINERAL SEM GAS 500 ML)   
14          (CROISSANT MUSSATRELA DE)   (AGUA MINERAL SEM GAS 500 ML)   
74                   (LARANJA 400 ML)                     (CROISSANT)   
88      (CROISSANT BRIE PARMA MEL DE)       (CROISSANT MUSSATRELA DE)   
4             (BOMBOLONI NUTELLA 80G)      (AGUA MINERAL S/GAS 500ML)   
128  (PIZZA AL TAGLIO PEPPERONI 210G)  (PIZZA AL TAGLIO GORGONZOLA E)   
18            (BOMBOLONI NUTELLA 80G)   (BOMBOLONI DOCE DE LEITE 80G)   
50            (COCA COLA LATA 350 ML)  (PIZZA AL TAGLIO GORGONZOLA E)   
58       (COCA COLA ZERO LATA 350 ML)    (SANDUICHE DE PEPERONI BRIE)   
24            (BOMBOLONI NUTELLA 80G)           (FOLHADO FRANGO 160G)   
2          (AGUA MINERAL C/GAS 500ML)                     (CROISSANT)   
28     (CAFE CATUAI VERMELHO G 200ML)                     (CROISSANT)   
44              (FOLHADO FRANGO 160G)         (COCA COLA LATA 350 ML)   
6          (AGUA MINERAL S/GAS 500ML)                     (CROISSANT)   
42      (CROISSANT BRIE PARMA MEL DE)         (COCA COLA LATA 350 ML)   
32             (CAFE COLMEIA G 200ML)                     (CROISSANT)   
124              (PASTEL DE NATA 60G)         (SUCO DE LARANJA 400ML)   
98     (SOURDOUGH AZEITONA E ALECRIM)       (FOCACCIA FORMAGGIO 246G)   
62                      (COOKIES 80G)           (FOLHADO FRANGO 160G)   
46            (COCA COLA LATA 350 ML)              (FOLHADO MACA 80G)   
30               (PASTEL DE NATA 60G)  (CAFE CATUAI VERMELHO G 200ML)   
10         (AGUA MINERAL S/GAS 500ML)    (SANDUICHE DE PEPERONI BRIE)   
60                      (COOKIES 80G)      (CROISSANT  AMENDOAS 100G)   
126              (PASTEL DE NATA 60G)     (TARTELETE DE MORANGO 120G)   
122              (PASTEL DE NATA 60G)  (QUICHE DE TOMATE SECO SALADA)   
38       (CAFE EQUILIBRADO CAPSULA P)            (PASTEL DE NATA 60G)   
102              (PASTEL DE NATA 60G)           (FOLHADO FRANGO 160G)   
16               (PASTEL DE NATA 60G)   (AGUA MINERAL SEM GAS 500 ML)   
104              (PASTEL DE NATA 60G)              (FOLHADO MACA 80G)   
78      (VH CAMINO DE CHILE CABERNET)                     (CROISSANT)   
120              (PASTEL DE NATA 60G)    (QUICHE DE FRANGO ALHO PORO)   
106      (QUICHE DE FRANGO ALHO PORO)              (FOLHADO MACA 80G)   
8                (PASTEL DE NATA 60G)      (AGUA MINERAL S/GAS 500ML)   
36       (CAFE EQUILIBRADO CAPSULA P)              (FOLHADO MACA 80G)   
54       (COCA COLA ZERO LATA 350 ML)                     (CROISSANT)   
26            (BOMBOLONI NUTELLA 80G)            (PASTEL DE NATA 60G)   
108                (FOLHADO MACA 80G)    (SANDUICHE DE PEPERONI BRIE)   
52            (COCA COLA LATA 350 ML)    (SANDUICHE DE PEPERONI BRIE)   
66                      (COOKIES 80G)            (PASTEL DE NATA 60G)   
90               (PASTEL DE NATA 60G)   (CROISSANT BRIE PARMA MEL DE)   
56               (PASTEL DE NATA 60G)    (COCA COLA ZERO LATA 350 ML)   
40            (COCA COLA LATA 350 ML)                     (CROISSANT)   
76    (MACA GENGIBRE ESPINAFRE LIMAO)                     (CROISSANT)   
48               (PASTEL DE NATA 60G)         (COCA COLA LATA 350 ML)   
110             (TORRADA FARINA 165G)              (FOLHADO MACA 80G)   
112              (PASTEL DE NATA 60G)      (FOLHADO MISTO COM TAMARA)   
84         (CROISSANT  AMENDOAS 100G)              (FOLHADO MACA 80G)   
70              (FOLHADO FRANGO 160G)                     (CROISSANT)   
64                      (COOKIES 80G)              (FOLHADO MACA 80G)   
22            (BOMBOLONI NUTELLA 80G)                     (CROISSANT)   
100             (FOLHADO FRANGO 160G)              (FOLHADO MACA 80G)   
116       (MINI PAIN AU CHOCOLAT 35G)            (PASTEL DE NATA 60G)   
80         

In [152]:
weekend_method_2 = apriori_results_method_2(dia_da_semana = 'FDS')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [153]:
weekend_method_2

antecedents  \
174              (ADICIONAL DE MUSSARELA, CROISSANT)   
0                           (ADICIONAL DE MUSSARELA)   
130                                (CROISSANT IFOOD)   
50                              (PAO SOURDOUGH OVOS)   
124                    (CROISSANT BRIE PARMA MEL DE)   
152                     (MINI CROISSANT 25G KIT C 5)   
134                        (CROISSANT MUSSATRELA DE)   
68                      (CAFE EQUILIBRADO CAPSULA P)   
175  (ADICIONAL DE MUSSARELA, ADICIONAL DE PRESUNTO)   
4                                        (CROISSANT)   
120                    (CROISSANT BRIE PARMA MEL DE)   
148                                 (LARANJA 400 ML)   
2                           (ADICIONAL DE MUSSARELA)   
26                         (CROISSANT MUSSATRELA DE)   
56                                  (LARANJA 400 ML)   
22                     (CROISSANT  TRADICIONAL 80 G)   
138                        (FOCACCIA FORMAGGIO 246G)   
14                    (CAFE CATUAI VERMELHO G 200ML)   
30                           (BOMBOLONI NUTELLA 80G)   
24                     (CROISSANT BRIE PARMA MEL DE)   
12                           (BOMBOLONI NUTELLA 80G)   
104                                 (LARANJA 400 ML)   
128                      (MINI PAIN AU CHOCOLAT 35G)   
142                            (TORRADA FARINA 165G)   
60                    (CAFE CATUAI VERMELHO G 200ML)   
140                   (SOURDOUGH AZEITONA E ALECRIM)   
94                             (TORRADA FARINA 165G)   
62                   (CAFE COLMEIA C/ LEITE G 200ML)   
156                   (SOURDOUGH AZEITONA E ALECRIM)   
52                  (CAFE CATUAI VERMELHO C/LEITE G)   
172                   (SOURDOUGH AZEITONA E ALECRIM)   
16                        (AGUA MINERAL S/GAS 500ML)   
54                    (CAFE CATUAI VERMELHO G 200ML)   
44                           (BOMBOLONI NUTELLA 80G)   
10                     (BOMBOLONI DOCE DE LEITE 80G)   
6                         (AGUA MINERAL C/GAS 500ML)   
146                             (PASTEL DE NATA 60G)   
98                     (COUVE LIMAO ABACAXI HORTELA)   
64                            (CAFE COLMEIA G 200ML)   
92                                     (COOKIES 80G)   
168                             (PASTEL DE NATA 60G)   
74                      (CAFE EQUILIBRADO CAPSULA P)   
36                     (BOMBOLONI DOCE DE LEITE 80G)   
20                        (AGUA MINERAL S/GAS 500ML)   
144                             (PASTEL DE NATA 60G)   
126                                (CROISSANT IFOOD)   
76                     (CAFE INTENSO CAPSULA P 50ML)   
160                             (PASTEL DE NATA 60G)   
8                               (PASTEL DE NATA 60G)   
114                                      (CROISSANT)   
58                              (PASTEL DE NATA 60G)   
86                                     (COOKIES 80G)   
96                                       (CROISSANT)   
162                   (QUICHE DE TOMATE SECO SALADA)   
82                      (COCA COLA ZERO LATA 350 ML)   
46                           (BOMBOLONI NUTELLA 80G)   
72                      (CAFE EQUILIBRADO CAPSULA P)   
122                             (PASTEL DE NATA 60G)   
32                                     (COOKIES 80G)   
40                     (BOMBOLONI DOCE DE LEITE 80G)   
88                                     (COOKIES 80G)   
80                              (PASTEL DE NATA 60G)   
118                             (PASTEL DE NATA 60G)   
116                       (CROISSANT  AMENDOAS 100G)   
28                              (PASTEL DE NATA 60G)   
164                             (PASTEL DE NATA 60G)   
166                             (PASTEL DE NATA 60G)   
158                      (MINI PAIN AU CHOCOLAT 35G)   
48                                       (CROISSANT)   
34                                 (CROISSANT IFOOD)   
106                  (MACA GENGIBRE ESPINAFRE LIMAO)   
42       

In [154]:
weekday_method_2 = apriori_results_method_2(dia_da_semana = 'DDS')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [155]:
weekday_method_2[:20]

antecedents  \
102              (ADICIONAL DE MUSSARELA, CROISSANT)   
104               (CROISSANT, ADICIONAL DE PRESUNTO)   
0                           (ADICIONAL DE MUSSARELA)   
26                              (PAO SOURDOUGH OVOS)   
86                      (MINI CROISSANT 25G KIT C 5)   
103  (ADICIONAL DE MUSSARELA, ADICIONAL DE PRESUNTO)   
4                                        (CROISSANT)   
12                     (CROISSANT BRIE PARMA MEL DE)   
2                           (ADICIONAL DE MUSSARELA)   
16                           (BOMBOLONI NUTELLA 80G)   
60                                  (LARANJA 400 ML)   
46                           (COCA COLA LATA 350 ML)   
32                   (CAFE COLMEIA C/ LEITE G 200ML)   
22                           (BOMBOLONI NUTELLA 80G)   
30                    (CAFE CATUAI VERMELHO G 200ML)   
34                            (CAFE COLMEIA G 200ML)   
74                    (SOURDOUGH AZEITONA E ALECRIM)   
100                   (SOURDOUGH AZEITONA E ALECRIM)   
28                  (CAFE CATUAI VERMELHO C/LEITE G)   
8                         (AGUA MINERAL S/GAS 500ML)   

                        consequents  antecedent support  consequent support  \
102         (ADICIONAL DE PRESUNTO)            0.009375            0.008398   
104        (ADICIONAL DE MUSSARELA)            0.007227            0.011719   
0           (ADICIONAL DE PRESUNTO)            0.011719            0.008398   
26   (BOWL DE IOGURTE FRUTAS AVEIA)            0.023633            0.024219   
86    (MINI CROISSANT PAIN DE CHOC)            0.047852            0.022852   
103                     (CROISSANT)            0.006836            0.188477   
4           (ADICIONAL DE PRESUNTO)            0.188477            0.008398   
12    (AGUA MINERAL SEM GAS 500 ML)            0.043945            0.033594   
2                       (CROISSANT)            0.011719            0.188477   
16    (BOMBOLONI DOCE DE LEITE 80G)            0.041016            0.046484   
60                      (CROISSANT)            0.031055            0.188477   
46   (PIZZA AL TAGLIO GORGONZOLA E)            0.037305            0.046875   
32                      (CROISSANT)            0.010937            0.188477   
22            (FOLHADO FRANGO 160G)            0.041016            0.050195   
30                      (CROISSANT)            0.025000            0.188477   
34                      (CROISSANT)            0.019922            0.188477   
74        (FOCACCIA FORMAGGIO 246G)            0.060547            0.046680   
100                (SOURDOUGH 369G)            0.060547            0.048242   
28                      (CROISSANT)            0.016016            0.188477   
8                       (CROISSANT)            0.043945            0.188477   

      support  confidence       lift  leverage  conviction  
102  0.006055    0.645833  76.899225  0.005976    2.799816  
104  0.006055    0.837838  71.495495  0.005970    6.094401  
0    0.006836    0.583333  69.457364  0.006738    2.379844  
26   0.006836    0.289256  11.943482  0.006264    1.372902  
86   0.005469    0.114286   5.001221  0.004375    1.103232  
103  0.006055    0.885714   4.699334  0.004766    7.100830  
4    0.007227    0.038342   4.565369  0.005644    1.031137  
12   0.006641    0.151111   4.498191  0.005164    1.138437  
2    0.009375    0.800000   4.244560  0.007166    4.057617  
16   0.007227    0.176190   3.790316  0.005320    1.157447  
60   0.019727    0.635220   3.370287  0.013873    2.224694  
46   0.005664    0.151832   3.239092  0.003915    1.123746  
32   0.005859    0.535714   2.842339  0.003798    1.747897  
22   0.005469    0.133333   2.656291  0.003410    1.095928  
30   0.011914    0.476562   2.528497  0.007202    1.550373  
34   0.008789    0.441176   2.340750  0.005034    1.452200  
74   0.006250    0.103226   2.211365  0.003424    1.063055  
100  0.005859    0.096774   2.006008  0.002938    1.053732  
28   0.006055    0.378049   2.005813  0.00303

In [156]:
weekend_morning_method_2 = apriori_results_method_2(dia_da_semana = 'FDS', hora_do_dia = 'manhã')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [157]:
weekend_morning_method_2[:20]

antecedents  \
266                (ADICIONAL DE MUSSARELA, CROISSANT)   
0                             (ADICIONAL DE MUSSARELA)   
142                                    (CIABATTA 123G)   
220                                   (CROISSANT OVOS)   
284     (PASTEL DE NATA 60G, AGUA MINERAL S/GAS 500ML)   
64                                   (CROISSANT IFOOD)   
128                       (CAFE EQUILIBRADO CAPSULA G)   
40                                    (CROISSANT OVOS)   
214                                  (CROISSANT IFOOD)   
238                       (MINI CROISSANT 25G KIT C 5)   
218                            (SUCO DE LARANJA 400ML)   
204                      (CROISSANT BRIE PARMA MEL DE)   
158                                (COOKIES 80G IFOOD)   
236                    (MACA GENGIBRE ESPINAFRE LIMAO)   
332                    (PAO SOURDOUGH OVOS, CROISSANT)   
285   (PASTEL DE NATA 60G, SANDUICHE DE PEPERONI BRIE)   
286  (AGUA MINERAL S/GAS 500ML, SANDUICHE DE PEPERO...   
42                          (CROISSANT OVOS BACON MEL)   
38                           (CROISSANT MUSSATRELA DE)   
302          (CAFE CATUAI VERMELHO G 200ML, CROISSANT)   

                          consequents  antecedent support  consequent support  \
266           (ADICIONAL DE PRESUNTO)            0.010824            0.009992   
0             (ADICIONAL DE PRESUNTO)            0.011657            0.009992   
142           (OVOS COM BACON E BRIE)            0.019983            0.024147   
220           (SUCO DE LARANJA 400ML)            0.017485            0.044963   
284      (SANDUICHE DE PEPERONI BRIE)            0.009159            0.067444   
64      (BOMBOLONI NUTELLA 80G IFOOD)            0.098251            0.006661   
128                  (CROISSANT OVOS)            0.043297            0.017485   
40      (AGUA MINERAL SEM GAS 500 ML)            0.017485            0.044963   
214            (SOURDOUGH 369G IFOOD)            0.098251            0.015820   
238     (MINI CROISSANT PAIN DE CHOC)            0.062448            0.024979   
218         (CROISSANT MUSSATRELA DE)            0.044963            0.036636   
204           (SUCO DE LARANJA 400ML)            0.049126            0.044963   
158                 (CROISSANT IFOOD)            0.011657            0.098251   
236           (OVOS COM BACON E BRIE)            0.041632            0.024147   
332                  (LARANJA 400 ML)            0.016653            0.064946   
285        (AGUA MINERAL S/GAS 500ML)            0.018318            0.059950   
286              (PASTEL DE NATA 60G)            0.009159            0.123231   
42      (AGUA MINERAL SEM GAS 500 ML)            0.047460            0.044963   
38      (AGUA MINERAL SEM GAS 500 ML)            0.036636            0.044963   
302  (CAFE CATUAI VERMELHO C/LEITE G)            0.034138            0.034138   

      support  confidence       lift  leverage  conviction  
266  0.005828    0.538462  53.891026  0.005720    2.145018  
0    0.005828    0.500000  50.041667  0.005712    1.980017  
142  0.006661    0.333333  13.804598  0.006179    1.463780  
220  0.007494    0.428571   9.531746  0.006708    1.671316  
284  0.005828    0.636364   9.435466  0.005211    2.564530  
64   0.005828    0.059322   8.905720  0.005174    1.055982  
128  0.005828    0.134615   7.698718  0.005071    1.135350  
40   0.005828    0.333333   7.413580  0.005042    1.432556  
214  0.010824    0.110169   6.963872  0.009270    1.106031  
238  0.009992    0.160000   6.405333  0.008432    1.160739  
218  0.009992    0.222222   6.065657  0.008344    1.238611  
204  0.013322    0.271186   6.031387  0.011113    1.310400  
158  0.006661    0.571429   5.815981  0.005516    2.104080  
236  0.005828    0.140000   5.797931  0.004823    1.134713  
332  0.005828    0.350000   5.389103  0.004747    1.438545  
285  0.005828    0.318182   5.307449  0.004730    1.378740  
286  0.005828    0.636364   5.164005  0.004700    2.411116  
42   0.010824    0.22807

In [158]:
weekday_afternoon_method_2 = apriori_results_method_2(dia_da_semana = 'DDS', hora_do_dia = 'tarde')

c:\Users\ctobr\miniconda3\envs\minimal_ds\lib\site-packages\mlxtend\frequent_patterns\fpcommon.py:111: DeprecationWarning:

DataFrames with non-bool types result in worse computationalperformance and their support might be discontinued in the future.Please use a DataFrame with bool type



In [159]:
weekday_afternoon_method_2[:20]

antecedents  \
146           (ADICIONAL DE MUSSARELA, CROISSANT)   
0                        (ADICIONAL DE MUSSARELA)   
148            (CROISSANT, ADICIONAL DE PRESUNTO)   
114                             (CROISSANT IFOOD)   
152   (BOMBOLONI NUTELLA 80G, PASTEL DE NATA 60G)   
154     (PASTEL DE NATA 60G, FOLHADO FRANGO 160G)   
4                                     (CROISSANT)   
42                   (CAFE EQUILIBRADO CAPSULA P)   
2                        (ADICIONAL DE MUSSARELA)   
16                        (BOMBOLONI NUTELLA 80G)   
153  (BOMBOLONI NUTELLA 80G, FOLHADO FRANGO 160G)   
124                  (MINI CROISSANT 25G KIT C 5)   
86                               (LARANJA 400 ML)   
52                  (CAFE INTENSO CAPSULA P 50ML)   
60                        (COCA COLA LATA 350 ML)   
159               (PASTEL DE NATA 60G, CROISSANT)   
18                  (BOMBOLONI DOCE DE LEITE 80G)   
28                        (BOMBOLONI NUTELLA 80G)   
116                (SOURDOUGH AZEITONA E ALECRIM)   
22                  (BOMBOLONI DOCE DE LEITE 80G)   

                       consequents  antecedent support  consequent support  \
146        (ADICIONAL DE PRESUNTO)            0.006613            0.005878   
0          (ADICIONAL DE PRESUNTO)            0.008082            0.005878   
148       (ADICIONAL DE MUSSARELA)            0.005143            0.008082   
114     (PASTEL DE NATA 60G IFOOD)            0.033064            0.014695   
152          (FOLHADO FRANGO 160G)            0.008082            0.053637   
154        (BOMBOLONI NUTELLA 80G)            0.013226            0.046289   
4          (ADICIONAL DE PRESUNTO)            0.161646            0.005878   
42   (CAFE INTENSO CAPSULA P 50ML)            0.043350            0.032329   
2                      (CROISSANT)            0.008082            0.161646   
16   (BOMBOLONI DOCE DE LEITE 80G)            0.046289            0.050698   
153           (PASTEL DE NATA 60G)            0.007348            0.156503   
124  (MINI CROISSANT PAIN DE CHOC)            0.058780            0.030860   
86                     (CROISSANT)            0.024982            0.161646   
52   (CROISSANT  TRADICIONAL 80 G)            0.032329            0.043350   
60    (SANDUICHE DE PEPERONI BRIE)            0.038207            0.055107   
159          (FOLHADO FRANGO 160G)            0.027921            0.053637   
18         (COCA COLA LATA 350 ML)            0.050698            0.038207   
28         (COCA COLA LATA 350 ML)            0.046289            0.038207   
116      (FOCACCIA FORMAGGIO 246G)            0.074945            0.041881   
22           (FOLHADO FRANGO 160G)            0.050698            0.053637   

      support  confidence        lift  leverage  conviction  
146  0.005143    0.777778  132.319444  0.005104    4.473549  
0    0.005878    0.727273  123.727273  0.005831    3.645114  
148  0.005143    1.000000  123.727273  0.005102         inf  
114  0.006613    0.200000   13.610000  0.006127    1.231631  
152  0.005143    0.636364   11.864259  0.004710    2.602498  
154  0.005143    0.388889    8.401235  0.004531    1.560617  
4    0.005143    0.031818    5.413068  0.004193    1.026793  
42   0.007348    0.169492    5.242681  0.005946    1.165155  
2    0.006613    0.818182    5.061570  0.005306    4.610948  
16   0.011756    0.253968    5.009432  0.009409    1.272469  
153  0.005143    0.700000    4.472770  0.003993    2.811658  
124  0.008082    0.137500    4.455655  0.006268    1.123641  
86   0.016899    0.676471    4.184893  0.012861    2.591276  
52   0.005143    0.159091    3.669877  0.003742    1.137637  
60   0.007348    0.192308    3.489744  0.005242    1.169868  
159  0.005143    0.184211    3.434391  0.003646    1.160058  
18   0.006613    0.130435    3.413880  0.004676    1.106062  
28   0.005878    0.126984    3.323565  0.004109    1.101690  
116  0.009552    0.127451    3.043172  0.006413    1.098069  
22   0.008082    0.159420    2.972206  0.0053

In [160]:
weekday_afternoon_method_2.groupby(by='antecedents')['lift'].sum().sort_values(ascending=False)

antecedents
(ADICIONAL DE MUSSARELA, CROISSANT)             132.319444
(ADICIONAL DE MUSSARELA)                        128.788843
(CROISSANT, ADICIONAL DE PRESUNTO)              123.727273
(BOMBOLONI NUTELLA 80G)                          17.929466
(PASTEL DE NATA 60G)                             17.655762
(CROISSANT IFOOD)                                16.151550
(COOKIES 80G)                                    15.015277
(SOURDOUGH AZEITONA E ALECRIM)                   12.046648
(BOMBOLONI NUTELLA 80G, PASTEL DE NATA 60G)      11.864259
(PASTEL DE NATA 60G, FOLHADO FRANGO 160G)        10.807043
(CAFE EQUILIBRADO CAPSULA P)                     10.160819
(COCA COLA LATA 350 ML)                           7.902987
(MINI CROISSANT 25G KIT C 5)                      7.571816
(BOMBOLONI DOCE DE LEITE 80G)                     7.551632
(CROISSANT)                                       5.413068
(CAFE INTENSO CAPSULA P 50ML)                     4.935269
(BOMBOLONI NUTELLA 80G, FOLHADO FRANGO 160G)